In [1]:
#Exercise 4 for small subset to check training behavior:

import pandas as pd;
from scipy.stats import zscore
import torch as torch;

import numpy as np

import torchvision.datasets as datasets


np.random.seed(42)
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')

n_classes = 10;
n_features = 28*28;


In [2]:
#read dataset:

full_train_dataset = datasets.MNIST(root='./data', train=True, download=True, transform=None)
full_test_dataset = datasets.MNIST(root='./data', train=False, download=True, transform=None)

x_train = full_train_dataset.data.numpy().reshape(-1,n_features).astype(dtype=np.float64)/255.0;
x_test = full_test_dataset.data.numpy().reshape(-1,n_features).astype(dtype=np.float64)/255.0;

y_train_cat = full_train_dataset.targets.numpy()
y_test_cat = full_test_dataset.targets.numpy()

In [3]:
dd_y=pd.DataFrame(data=y_train_cat)
y_train=pd.get_dummies(dd_y,columns = list(dd_y.columns)).to_numpy().astype(dtype=float);

dd_y=pd.DataFrame(data=y_test_cat)
y_test=pd.get_dummies(dd_y,columns = list(dd_y.columns)).to_numpy().astype(dtype=float);


# split the dataset
permutation = np.random.permutation(x_train.shape[0]);
x_train=x_train[permutation,:]
y_train=y_train[permutation,:]

# small subset:
subset_size = 2000;
x_train=x_train[:subset_size,:]
y_train=y_train[:subset_size,:]


n_train=x_train.shape[0];

# create tensor variables for data, we do not need gradient w.r.t. to them
t_x_test=torch.tensor(x_test,requires_grad=False,device=device);
t_y_test=torch.tensor(y_test,requires_grad=False,device=device);

In [4]:
#define starting value of weights W for gradient descent
init_std_dev = 0.01;
initialW=init_std_dev*np.random.randn(n_features,n_classes)
# create a PyTorch tensor variable for W and b. 
# we will be optimizing over W, b, finding their best value using gradient descent,
#so we need gradient enabled
W = torch.tensor(initialW,requires_grad=True,device=device);
b = torch.zeros((1,n_classes),requires_grad=True,device=device);
# this optimizer will do gradient descent for us
learning_rate = 0.01;
#optimizer = torch.optim.SGD([W,b],lr=learning_rate)
optimizer = torch.optim.Adam([W,b],lr=learning_rate)
n_epochs = 10000;
batch_size = 64;


In [5]:
for i in range(n_epochs):

    
    permutation = np.random.permutation(x_train.shape[0]);
    x_train=x_train[permutation,:]
    y_train=y_train[permutation,:]

    accuracy = 0.0;

    #looping over batch_size
    for j in range(0,n_train,batch_size):
        t_x_train = torch.tensor(x_train[j:j+batch_size,:],requires_grad=False,device=device);
        t_y_train = torch.tensor(y_train[j:j+batch_size,:],requires_grad=False,device=device);

        # clear previous gradient calculations
        optimizer.zero_grad();
        
        # calculate model predictions
        linear_predictions = torch.matmul(t_x_train,W)+b
        activations =  torch.exp(linear_predictions);
    
        #Passing through softmax
        sum_activations = torch.sum(activations,dim=1,keepdim=True)
        normalized_activations = torch.div(activations, sum_activations);
        cross_entropy_loss = torch.sum(torch.multiply(t_y_train,torch.log(normalized_activations)),dim=1 )
        risk = -1.0 * torch.mean(cross_entropy_loss );

        # calculate gradients
        risk.backward();
        
        # take the gradient step
        optimizer.step();
        

        batch_risk=risk.item();

        true_class = np.argmax(t_y_train.detach().cpu().numpy(),axis=1)
        pred_class = np.argmax(normalized_activations.detach().cpu().numpy(),axis=1)
        accuracy += np.count_nonzero(true_class == pred_class);
        
    # calculate test set risk and accuracy
    #  turn off gradeints 
        
    with (torch.no_grad()):
      linear_predictions = torch.matmul(t_x_test,W)+b
      activations =  torch.exp(linear_predictions);
    
      #Passing through softmax
      sum_activations = torch.sum(activations,dim=1,keepdim=True)
      test_normalized_activations = torch.div(activations, sum_activations);
      cross_entropy_loss = torch.sum(torch.multiply(t_y_test,torch.log(test_normalized_activations)),dim=1 )
    
      test_risk = -1.0 * torch.mean(cross_entropy_loss );
    
      test_true_class = np.argmax(t_y_test.detach().cpu().numpy(),axis=1)
      test_pred_class = np.argmax(test_normalized_activations.detach().cpu().numpy(),axis=1)
      test_accuracy = np.count_nonzero(test_true_class == test_pred_class)/test_pred_class.shape[0];
      test_error = 1.0 - test_accuracy;
        
    accuracy = accuracy / float(x_train.shape[0])
    print(i,batch_risk,test_risk.item(),accuracy,test_accuracy)

0 0.4954644927472347 0.4787894673524728 0.7265 0.8604
1 0.14098629358278753 0.39005622256024736 0.8835 0.8909
2 0.18195637354408847 0.3705316615281263 0.9195 0.896
3 0.16252221302494238 0.37319003712443877 0.932 0.8924
4 0.14025770293102371 0.38021019844022824 0.943 0.8891
5 0.059397445847301764 0.37719584145967583 0.9535 0.8919
6 0.11373722580799134 0.3599227413178643 0.957 0.8981
7 0.18917248751080434 0.3631094858644098 0.9685 0.8964
8 0.34752791909902764 0.3674165429557507 0.972 0.8956
9 0.07511979860325063 0.3742600278586714 0.977 0.8949
10 0.13061287744260439 0.38114909965841953 0.9775 0.8931
11 0.2413975324682765 0.37892915511915254 0.983 0.8947
12 0.47730117635045693 0.4044803664569875 0.9855 0.8897
13 0.1123495298529271 0.39856523956890316 0.9855 0.8911
14 0.11419401310397032 0.39148217432297067 0.9885 0.8945
15 0.08945765493137228 0.40360432561322046 0.991 0.892
16 0.06274908521404138 0.4059814564495232 0.992 0.8944
17 0.0573175465665785 0.41677680221572555 0.9935 0.8918
18 0.

151 0.0009555860585485736 0.7470335097663485 1.0 0.8864
152 0.0015594433925956454 0.7494488956488249 1.0 0.8869
153 0.0027733588377180387 0.7511204615824492 1.0 0.8869
154 0.0027524598595265177 0.751717445500077 1.0 0.8861
155 0.0018778959984577985 0.7546519591578646 1.0 0.8851
156 0.0012060419195410986 0.7559611464706226 1.0 0.8856
157 0.0014333086712704241 0.756881673378039 1.0 0.8867
158 0.0015524824150196126 0.7641132245693594 1.0 0.8855
159 0.0008357374454148849 0.7623111797905815 1.0 0.8863
160 0.0007249954089229443 0.7655428010574021 1.0 0.8854
161 0.0003305098096465346 0.7641091375174612 1.0 0.8863
162 0.004188899169304553 0.7650333569699058 1.0 0.8855
163 0.001070772081374178 0.7689324934159544 1.0 0.8854
164 0.0014620282869274102 0.7712043418260237 1.0 0.8865
165 0.001660382899660283 0.7737991744178294 1.0 0.8867
166 0.0015597666180591717 0.7760603892021951 1.0 0.8855
167 0.001819373697566841 0.776020304888701 1.0 0.8856
168 0.0019359695696073477 0.7795910197716801 1.0 0.8855

299 0.0001129253584188121 1.014248545525296 1.0 0.8836
300 0.00038892467786850457 1.0139684378630343 1.0 0.884
301 5.6127057405601424e-05 1.0149551987941727 1.0 0.8846
302 5.962311669450171e-05 1.0190155720850635 1.0 0.8837
303 0.00013947416077862116 1.0200125584423563 1.0 0.884
304 0.00017905982456357383 1.0227167417270269 1.0 0.8841
305 0.00013487335856809262 1.022830413007759 1.0 0.8837
306 0.0002145666131406224 1.028532700710947 1.0 0.8839
307 8.398533687017866e-05 1.025385729839591 1.0 0.8837
308 4.663257779725955e-05 1.0313524582854985 1.0 0.8848
309 0.00028290774765297815 1.0313993549482265 1.0 0.8846
310 0.0001486440418383754 1.0339737407760858 1.0 0.8838
311 7.684875778217694e-05 1.038449810922054 1.0 0.8841
312 3.5804093579628e-05 1.0330300932030656 1.0 0.8835
313 6.555304107950316e-05 1.0400278258812496 1.0 0.8845
314 0.00013238597112769326 1.0399525281150934 1.0 0.8845
315 8.605214729815884e-05 1.0416142885375401 1.0 0.8843
316 2.8616685772320463e-05 1.0412410066550983 1.0 

448 1.4814665019566075e-05 1.2807211656360278 1.0 0.8823
449 1.2220502075442424e-05 1.28153345984387 1.0 0.8825
450 2.6445333731192033e-05 1.2849167784022046 1.0 0.8822
451 9.618739008167114e-06 1.2849249681127464 1.0 0.883
452 1.4168483409468188e-05 1.2914858878184539 1.0 0.8822
453 5.416621112623614e-06 1.2927850685137947 1.0 0.8818
454 1.237070367852192e-05 1.2915537003109603 1.0 0.8825
455 2.501716062929034e-05 1.291371882590862 1.0 0.8822
456 1.695837598216002e-05 1.2978543960468436 1.0 0.8821
457 1.1945620727225745e-05 1.2969103827239108 1.0 0.8821
458 2.386839076742577e-05 1.3007015899955607 1.0 0.8821
459 1.027267300647042e-05 1.303310791974381 1.0 0.8822
460 2.175460871111771e-06 1.3047360846271936 1.0 0.8823
461 2.237320834093852e-05 1.306528596322754 1.0 0.8816
462 1.4788457454238489e-05 1.3100475242616771 1.0 0.8817
463 1.7305605530252748e-05 1.3123404230326334 1.0 0.8813
464 1.3613508802717247e-05 1.3102009569558344 1.0 0.8827
465 8.012635661797817e-06 1.312515368965521 1.

596 6.557132723249379e-07 1.5485496466584612 1.0 0.8809
597 8.433406714493387e-07 1.5529690945020667 1.0 0.8813
598 6.848384669595128e-07 1.5533648199189944 1.0 0.881
599 1.0959380321595605e-06 1.5565861851316314 1.0 0.8809
600 1.686233491822929e-06 1.5564392647030882 1.0 0.881
601 2.459384852526609e-06 1.5582116554465044 1.0 0.8811
602 8.746612488039001e-07 1.5597500270883242 1.0 0.8811
603 2.6933232929577235e-06 1.5596350454357817 1.0 0.8806
604 3.7341826952876083e-07 1.5637143394347635 1.0 0.8811
605 1.7843886142868458e-06 1.5680036034020661 1.0 0.8816
606 1.4534760145487973e-06 1.5640565844688172 1.0 0.8807
607 4.1658202696090327e-07 1.5684129037890693 1.0 0.8805
608 1.7724630484291702e-06 1.5727075809746012 1.0 0.8807
609 1.5120252887955125e-06 1.5718490065736335 1.0 0.8807
610 1.029081372671214e-06 1.574852079263762 1.0 0.8816
611 1.43779578159225e-06 1.5739660414559276 1.0 0.8811
612 9.77685914216917e-07 1.580036622910398 1.0 0.8812
613 4.051975925178668e-07 1.5786289694948532 1

...

9342 3.4148863620089874e-10 2.536647176468518 1.0 0.878
9343 2.443867956691536e-10 2.5366636371413596 1.0 0.878
9344 2.2620157844945882e-10 2.536680978445064 1.0 0.878
9345 9.673565423575283e-11 2.5366883498530313 1.0 0.878
9346 1.166970271092563e-10 2.5367271192899987 1.0 0.878
9347 5.443236630434988e-10 2.5367368336968044 1.0 0.878
9348 3.284246140794855e-10 2.5367978953406136 1.0 0.878
9349 1.0842077935849426e-10 2.536768671814686 1.0 0.878
9350 2.848831797251453e-10 2.536788446121025 1.0 0.878
9351 4.2297817364476627e-10 2.536842188113077 1.0 0.878
9352 2.395848104230243e-10 2.5368709335253414 1.0 0.878
9353 1.6421791014786668e-10 2.536875003901507 1.0 0.878
9354 4.464330507101937e-10 2.5368553307287276 1.0 0.878
9355 4.6109526662227736e-10 2.5368731460965153 1.0 0.878
9356 2.4060711074136875e-10 2.536866409382131 1.0 0.878
9357 1.8193454390141788e-10 2.5368607102397633 1.0 0.878
9358 1.7485016221059039e-10 2.536971675306962 1.0 0.878
9359 3.3890204560615164e-10 2.536878636285978 1

9488 1.892463131528661e-10 2.538713476305896 1.0 0.8781
9489 4.0521661755130996e-10 2.5387804845651853 1.0 0.8781
9490 2.7862896725114163e-10 2.5388311992394206 1.0 0.8781
9491 2.852520166476191e-10 2.538822519490131 1.0 0.8781
9492 3.1310799797977984e-10 2.538886485520041 1.0 0.878
9493 2.1739794001615033e-10 2.538877266280746 1.0 0.878
9494 1.969130276235037e-10 2.5388689022825166 1.0 0.8781
9495 9.837728551422809e-11 2.5388624676756395 1.0 0.8781
9496 2.2857357685207406e-10 2.5388823762660153 1.0 0.8781
9497 1.1480093961824475e-10 2.5388746647740192 1.0 0.8781
9498 3.9255772247223506e-11 2.5388953871199234 1.0 0.8781
9499 2.0129577874053817e-10 2.5389164030415254 1.0 0.8781
9500 3.023711421592018e-10 2.5389063051189162 1.0 0.878
9501 7.798754697996961e-12 2.5389291894472086 1.0 0.8781
9502 3.7320685461325325e-10 2.538920188283 1.0 0.8781
9503 7.104806683360078e-10 2.5389769427884588 1.0 0.878
9504 1.0579295774995684e-10 2.5388695002261965 1.0 0.878
9505 1.2619104376178203e-10 2.5389

9634 1.7793018461896057e-10 2.540868346822976 1.0 0.8779
9635 1.6321294323569002e-10 2.5408841454462228 1.0 0.8779
9636 1.2506925361830082e-10 2.540898447900673 1.0 0.8779
9637 5.248162533791826e-10 2.5408922482642953 1.0 0.8779
9638 3.099648595290193e-10 2.5410242219164245 1.0 0.8779
9639 1.2078126002757063e-10 2.5410259793151484 1.0 0.8779
9640 3.130180769199396e-10 2.5410169849914266 1.0 0.8779
9641 4.1436434175873994e-10 2.5410260659938064 1.0 0.8779
9642 3.725399505106251e-10 2.5410253171556776 1.0 0.8779
9643 3.606995190961985e-10 2.5410571257464727 1.0 0.8779
9644 1.8679716117131823e-10 2.541082754483209 1.0 0.8779
9645 1.198542585272149e-10 2.54108124063543 1.0 0.8779
9646 2.6489230970095684e-10 2.5410695861476946 1.0 0.8779
9647 2.6901428337247034e-10 2.5410959074317607 1.0 0.878
9648 3.3245993475026515e-10 2.541111623432583 1.0 0.8779
9649 1.4165580519067023e-10 2.5411061908186356 1.0 0.878
9650 1.3295550080586054e-10 2.541184148694508 1.0 0.8779
9651 1.829437644006038e-10 2.

9779 1.2440783823525411e-10 2.5427035879372903 1.0 0.878
9780 3.495918000985455e-10 2.5427689064703514 1.0 0.8779
9781 8.293785104899849e-11 2.5427168712193167 1.0 0.878
9782 2.7286584811995684e-10 2.542699149867308 1.0 0.878
9783 3.4397812429303345e-10 2.5427306535880163 1.0 0.878
9784 2.603149433335691e-10 2.5427631445781174 1.0 0.8779
9785 2.444787290577737e-10 2.5427734518020273 1.0 0.878
9786 1.6233796949165477e-10 2.5428025047119385 1.0 0.8779
9787 4.812119109533372e-10 2.542828457667894 1.0 0.8779
9788 7.265010123624591e-11 2.5428926426146665 1.0 0.8779
9789 9.292668025620992e-11 2.542892012942248 1.0 0.8779
9790 2.435769642494923e-10 2.5429128393505342 1.0 0.8779
9791 1.8644101546662758e-10 2.5428729359626354 1.0 0.8779
9792 1.4296602800829128e-10 2.5429182493301807 1.0 0.8779
9793 1.3750930950574993e-11 2.5429236545540386 1.0 0.878
9794 1.848441400829917e-10 2.5429231067004125 1.0 0.8779
9795 1.4983360393462148e-10 2.5430074631855377 1.0 0.8779
9796 2.5981292829015386e-10 2.54

9925 1.1379847068033033e-10 2.5446865314477387 1.0 0.8779
9926 1.4181730794425646e-10 2.544691312203166 1.0 0.8779
9927 1.46602847960441e-10 2.5446931356431914 1.0 0.8779
9928 1.4316550032597158e-10 2.544682328647706 1.0 0.8779
9929 2.2437367945900258e-10 2.544758047152686 1.0 0.8779
9930 5.243104497308868e-10 2.5447586897875283 1.0 0.8779
9931 1.515120252469665e-10 2.544853514281829 1.0 0.8779
9932 7.129462993476778e-11 2.544832126552961 1.0 0.8779
9933 1.9893401514729864e-10 2.544878249499821 1.0 0.8779
9934 4.1363209419223303e-10 2.5448916782801856 1.0 0.8779
9935 3.379551848569543e-10 2.544878864318043 1.0 0.8779
9936 1.6016155771536046e-10 2.5448748713096805 1.0 0.8779
9937 1.5185328698053868e-10 2.544898540681357 1.0 0.8779
9938 1.9627757065253295e-10 2.5449460352071256 1.0 0.8779
9939 2.0726025772806623e-10 2.5449208737265914 1.0 0.8779
9940 7.914986029653016e-11 2.544924454342572 1.0 0.8779
9941 1.7168278608821593e-10 2.5449209822931165 1.0 0.8779
9942 1.3764686616386399e-10 2.

In [8]:
dd_y=pd.DataFrame(data=y_train_cat)
y_train=pd.get_dummies(dd_y,columns = list(dd_y.columns)).to_numpy().astype(dtype=float);

dd_y=pd.DataFrame(data=y_test_cat)
y_test=pd.get_dummies(dd_y,columns = list(dd_y.columns)).to_numpy().astype(dtype=float);


# split the dataset
permutation = np.random.permutation(x_train.shape[0]);
x_train=x_train[permutation,:]
y_train=y_train[permutation,:]

# small subset:
subset_size = 500;
x_train=x_train[:subset_size,:]
y_train=y_train[:subset_size,:]


n_train=x_train.shape[0];

# create tensor variables for data, we do not need gradient w.r.t. to them
t_x_test=torch.tensor(x_test,requires_grad=False,device=device);
t_y_test=torch.tensor(y_test,requires_grad=False,device=device);

In [9]:
#define starting value of weights W for gradient descent
init_std_dev = 0.01;
initialW=init_std_dev*np.random.randn(n_features,n_classes)
# create a PyTorch tensor variable for W and b. 
# we will be optimizing over W, b, finding their best value using gradient descent,
#so we need gradient enabled
W = torch.tensor(initialW,requires_grad=True,device=device);
b = torch.zeros((1,n_classes),requires_grad=True,device=device);
# this optimizer will do gradient descent for us
learning_rate = 0.01;
#optimizer = torch.optim.SGD([W,b],lr=learning_rate)
optimizer = torch.optim.Adam([W,b],lr=learning_rate)
n_epochs = 10000;
batch_size = 64;


In [10]:
for i in range(n_epochs):

    
    permutation = np.random.permutation(x_train.shape[0]);
    x_train=x_train[permutation,:]
    y_train=y_train[permutation,:]

    accuracy = 0.0;

    #looping over batch_size
    for j in range(0,n_train,batch_size):
        t_x_train = torch.tensor(x_train[j:j+batch_size,:],requires_grad=False,device=device);
        t_y_train = torch.tensor(y_train[j:j+batch_size,:],requires_grad=False,device=device);

        # clear previous gradient calculations
        optimizer.zero_grad();
        
        # calculate model predictions
        linear_predictions = torch.matmul(t_x_train,W)+b
        activations =  torch.exp(linear_predictions);
    
        #Passing through softmax
        sum_activations = torch.sum(activations,dim=1,keepdim=True)
        normalized_activations = torch.div(activations, sum_activations);
        cross_entropy_loss = torch.sum(torch.multiply(t_y_train,torch.log(normalized_activations)),dim=1 )
        risk = -1.0 * torch.mean(cross_entropy_loss );

        # calculate gradients
        risk.backward();
        
        # take the gradient step
        optimizer.step();
        

        batch_risk=risk.item();

        true_class = np.argmax(t_y_train.detach().cpu().numpy(),axis=1)
        pred_class = np.argmax(normalized_activations.detach().cpu().numpy(),axis=1)
        accuracy += np.count_nonzero(true_class == pred_class);
        
    # calculate test set risk and accuracy
    #  turn off gradeints 
        
    with (torch.no_grad()):
      linear_predictions = torch.matmul(t_x_test,W)+b
      activations =  torch.exp(linear_predictions);
    
      #Passing through softmax
      sum_activations = torch.sum(activations,dim=1,keepdim=True)
      test_normalized_activations = torch.div(activations, sum_activations);
      cross_entropy_loss = torch.sum(torch.multiply(t_y_test,torch.log(test_normalized_activations)),dim=1 )
    
      test_risk = -1.0 * torch.mean(cross_entropy_loss );
    
      test_true_class = np.argmax(t_y_test.detach().cpu().numpy(),axis=1)
      test_pred_class = np.argmax(test_normalized_activations.detach().cpu().numpy(),axis=1)
      test_accuracy = np.count_nonzero(test_true_class == test_pred_class)/test_pred_class.shape[0];
      test_error = 1.0 - test_accuracy;
        
    accuracy = accuracy / float(x_train.shape[0])
    print(i,batch_risk,test_risk.item(),accuracy,test_accuracy)

0 2.623476700594129 2.383704800626039 0.076 0.1312
1 2.043195867654637 2.4894968098356562 0.242 0.1437
2 2.085634018345386 2.41856547476235 0.338 0.1107
3 1.8784910960240806 2.468554264892348 0.372 0.1375
4 1.9144408307910774 2.4381312674647306 0.458 0.1282
5 1.7393094782572176 2.512954370526259 0.47 0.1207
6 1.5938111673743913 2.5199087913629534 0.516 0.1309
7 1.406348807114046 2.5937420589518396 0.534 0.1229
8 1.5191992981121936 2.5466277892933804 0.572 0.1204
9 1.340613875131002 2.6139481179672295 0.618 0.1147
10 1.3215757928335952 2.6279518300259967 0.604 0.1163
11 1.3463514442453817 2.65705560161637 0.618 0.1271
12 1.1669357715125892 2.6820247814770415 0.648 0.1227
13 1.2065028561876905 2.7108648849449577 0.676 0.1152
14 1.0919036072019102 2.7445582968003075 0.67 0.1269
15 1.059151844494644 2.767746533137105 0.692 0.1111
16 1.1411007493811292 2.7717746875968605 0.712 0.1264
17 1.0003939122665195 2.8468378348711267 0.734 0.1122
18 1.1287367412013074 2.8068473474735374 0.744 0.1312


154 0.10145734800110894 5.273351121584246 0.996 0.1263
155 0.11063370247774519 5.308451962685178 0.998 0.124
156 0.09236741126196575 5.320521684132644 0.996 0.1244
157 0.08953096076295591 5.320576853197088 0.998 0.1248
158 0.09891652706067955 5.347763865612071 0.998 0.123
159 0.0986663863782565 5.340027067317704 0.998 0.1261
160 0.1050749666430003 5.364385585278499 0.998 0.1249
161 0.12061308435872108 5.372675559439466 0.998 0.1232
162 0.11460125494978204 5.4001112293241444 0.998 0.1248
163 0.12837098387061102 5.418301854537804 0.998 0.1223
164 0.10552625931161028 5.383544435088955 0.998 0.126
165 0.1158838621498699 5.422898855680965 0.998 0.1248
166 0.11701043086286887 5.424634770121226 0.998 0.125
167 0.1138028838380618 5.447110685102171 0.998 0.1265
168 0.1057812252165614 5.442432419754499 0.998 0.1248
169 0.09537261609775632 5.469065459190789 0.998 0.1249
170 0.09126458769075524 5.468508369544068 0.998 0.1265
171 0.10961041832357993 5.476723242013657 0.998 0.1253
172 0.108230357276

309 0.03274889929354253 6.727850665844153 1.0 0.1226
310 0.0366024162370282 6.7561899835120744 1.0 0.1225
311 0.04090316135305743 6.751141316741294 1.0 0.1229
312 0.027540602818433804 6.755046468438694 1.0 0.1234
313 0.031699923300127754 6.765230462143277 1.0 0.1231
314 0.02549933490541112 6.771617794177498 1.0 0.1233
315 0.026278463770501696 6.787053245552015 1.0 0.1222
316 0.026523804595992143 6.790770223888385 1.0 0.1225
317 0.029893596035382115 6.798079363008448 1.0 0.1234
318 0.03949959552108636 6.79568103747689 1.0 0.124
319 0.029202930236296967 6.808600087189622 1.0 0.1222
320 0.02798669258983128 6.818656540257949 1.0 0.1226
321 0.03081995664520989 6.825765949399174 1.0 0.1234
322 0.036925238499387864 6.833011395582432 1.0 0.1213
323 0.022147803798152194 6.841153870499901 1.0 0.1223
324 0.031942701170066756 6.851717699683396 1.0 0.1224
325 0.023633965963937135 6.86275975603759 1.0 0.1222
326 0.03208633571084008 6.873842159988999 1.0 0.1217
327 0.034304829157475784 6.850463340722

468 0.0130247751207104 7.794930729573212 1.0 0.1216
469 0.018236180520965137 7.806766355024481 1.0 0.1218
470 0.00971203098438787 7.818676612716395 1.0 0.1223
471 0.012202484212145596 7.810437651669068 1.0 0.1229
472 0.011011066685986986 7.816841989962353 1.0 0.1225
473 0.013232087048723888 7.8335235719230925 1.0 0.1219
474 0.011594106927097246 7.846764227534602 1.0 0.1207
475 0.01359779289469832 7.841696955730699 1.0 0.1228
476 0.011165395411717191 7.839526214526667 1.0 0.1224
477 0.011893527135626386 7.867028882364457 1.0 0.1211
478 0.014358252766784967 7.867273011841148 1.0 0.1223
479 0.01513667761779163 7.867214049699731 1.0 0.1227
480 0.01095461947479021 7.872753771558532 1.0 0.1224
481 0.012021147623200147 7.8889625025210615 1.0 0.1209
482 0.012465690777051478 7.888913786243489 1.0 0.1224
483 0.01189614166112283 7.880228514725063 1.0 0.1227
484 0.01223376426893665 7.8955769172705095 1.0 0.1221
485 0.012650295978982616 7.9112197802900805 1.0 0.1216
486 0.010654108517025298 7.90531

626 0.005054369030074284 8.695529136320111 1.0 0.1215
627 0.005186399593661215 8.707391937743257 1.0 0.1223
628 0.005711632322312995 8.715686931117999 1.0 0.1219
629 0.004905755515545571 8.713912150520244 1.0 0.1219
630 0.006188334192783259 8.72226908577165 1.0 0.1212
631 0.004788877957355553 8.732690325063171 1.0 0.1214
632 0.005407400058763416 8.73377835592999 1.0 0.1223
633 0.0061321088533066075 8.73965043028949 1.0 0.1209
634 0.0054805038578805915 8.747837480558802 1.0 0.1213
635 0.0071639578631185466 8.74521762844521 1.0 0.1221
636 0.006939717719004243 8.755518150215677 1.0 0.1219
637 0.0061052195390024575 8.75982604816345 1.0 0.1219
638 0.005365860292445158 8.760182429955249 1.0 0.122
639 0.005298806561563726 8.771562438691344 1.0 0.1208
640 0.005066954892695168 8.780381955328645 1.0 0.1209
641 0.006418654648087206 8.785595085683557 1.0 0.1221
642 0.005837244145902911 8.789778200615975 1.0 0.1215
643 0.005391843269346672 8.793164688016047 1.0 0.1217
644 0.005737482707258346 8.804

...

9311 3.6460716873070117e-09 26.091914495264145 1.0 0.1201
9312 4.639033544680929e-09 26.091773483132954 1.0 0.1201
9313 3.7525748721186945e-09 26.092186128362904 1.0 0.12
9314 4.01153822366036e-09 26.092526135110777 1.0 0.1201
9315 4.147185899022081e-09 26.09249331936237 1.0 0.12
9316 3.3046394633389964e-09 26.09274470168517 1.0 0.12
9317 3.796607576588403e-09 26.09310879896658 1.0 0.1201
9318 3.152993377933594e-09 26.09361671624223 1.0 0.1202
9319 3.818097298213101e-09 26.09348893325882 1.0 0.1201
9320 3.3363758934194006e-09 26.093694696849514 1.0 0.12
9321 4.552424424705044e-09 26.093872121347573 1.0 0.1201
9322 4.017273961942679e-09 26.09357929716157 1.0 0.1201
9323 3.308636932002535e-09 26.093916583468935 1.0 0.12
9324 3.2114291316573444e-09 26.093776205937942 1.0 0.1201
9325 4.1344593493365755e-09 26.09422795999608 1.0 0.1201
9326 3.1707081094874336e-09 26.094602600394342 1.0 0.12
9327 3.2284558283141253e-09 26.094628088772602 1.0 0.1201
9328 3.2102357869082995e-09 26.094509620853

9458 3.932027340576217e-09 26.120084562175553 1.0 0.1201
9459 3.6947978480193882e-09 26.119406397032336 1.0 0.1201
9460 3.043462549156803e-09 26.12002164128961 1.0 0.1201
9461 3.179193065490295e-09 26.12047406123161 1.0 0.1201
9462 3.2463772040307838e-09 26.12087806346709 1.0 0.1201
9463 3.956643072540417e-09 26.121041389331122 1.0 0.1201
9464 3.121762382895155e-09 26.1210880230412 1.0 0.1201
9465 4.356764942032032e-09 26.12073852150973 1.0 0.1201
9466 2.9680227160079035e-09 26.12128009391869 1.0 0.1201
9467 3.0385219063334996e-09 26.1216556680644 1.0 0.1201
9468 3.890755225624093e-09 26.122352512191128 1.0 0.1201
9469 3.790043537448514e-09 26.12241225920871 1.0 0.1201
9470 3.113410260963662e-09 26.122672159503274 1.0 0.1201
9471 2.946020687586447e-09 26.123024989087817 1.0 0.1201
9472 3.892984823902513e-09 26.122235228180962 1.0 0.1201
9473 3.739709755182498e-09 26.123186573889217 1.0 0.1201
9474 3.5589475418423796e-09 26.123544632643064 1.0 0.1202
9475 3.612359777521705e-09 26.123208

9604 3.6568318153933227e-09 26.14808056474423 1.0 0.1201
9605 3.040905098719283e-09 26.147981306791927 1.0 0.1201
9606 2.5844721388082924e-09 26.14827680452203 1.0 0.1201
9607 3.989840191023166e-09 26.1481941345708 1.0 0.1201
9608 3.745689227796673e-09 26.148998857787248 1.0 0.1201
9609 2.750082707788981e-09 26.148725265416804 1.0 0.1201
9610 3.4413822696431956e-09 26.14870429450654 1.0 0.1201
9611 3.773558966899983e-09 26.14891713538481 1.0 0.1201
9612 3.2418213545007934e-09 26.1495733495238 1.0 0.1201
9613 3.6218848786548126e-09 26.14948114818422 1.0 0.1201
9614 3.758546003869417e-09 26.14952703572839 1.0 0.1201
9615 3.537852321504548e-09 26.149538365048308 1.0 0.1201
9616 3.603727637526856e-09 26.15019778025191 1.0 0.1201
9617 2.9710374762278732e-09 26.150655157138857 1.0 0.1201
9618 3.07714590016757e-09 26.150899147617917 1.0 0.1201
9619 3.0166840783147568e-09 26.15061177075992 1.0 0.1201
9620 3.2882214779654227e-09 26.15061977886675 1.0 0.1201
9621 3.462685010913598e-09 26.1508173

9754 3.305679382107962e-09 26.175626972082544 1.0 0.12
9755 3.5236001543617215e-09 26.175867659605 1.0 0.1201
9756 3.1408922433732814e-09 26.17565318476935 1.0 0.1201
9757 3.3433433445942713e-09 26.176111841212244 1.0 0.1201
9758 3.1141460436453624e-09 26.176208669660586 1.0 0.12
9759 2.7672476839233693e-09 26.176575783420752 1.0 0.1201
9760 3.734268195786051e-09 26.176544371095922 1.0 0.12
9761 2.971094429051063e-09 26.176779347181174 1.0 0.1201
9762 2.6817169906627455e-09 26.176959270442765 1.0 0.12
9763 3.5510521450237273e-09 26.17745273558328 1.0 0.12
9764 2.934648562558182e-09 26.17744925922776 1.0 0.1201
9765 2.9483553119521917e-09 26.177903681770793 1.0 0.12
9766 3.6366085590813524e-09 26.17861513854073 1.0 0.1201
9767 3.7888049630488295e-09 26.17890937656798 1.0 0.12
9768 2.704499356107315e-09 26.17903105533764 1.0 0.1201
9769 3.2700665607597712e-09 26.178527917920377 1.0 0.1202
9770 4.226920203190802e-09 26.179159588004957 1.0 0.1202
9771 3.2352389482504325e-09 26.179317998618

9901 2.9353610000622735e-09 26.201890829181394 1.0 0.12
9902 3.636808151069576e-09 26.20209150232899 1.0 0.1201
9903 3.517982180581942e-09 26.20265346162698 1.0 0.1201
9904 3.17449870889661e-09 26.202787162652374 1.0 0.12
9905 2.982240903045308e-09 26.20344823429206 1.0 0.1201
9906 3.505790707762171e-09 26.2032694660477 1.0 0.12
9907 3.2102406581887734e-09 26.203510016825522 1.0 0.12
9908 2.8326034588453523e-09 26.20390928176943 1.0 0.1201
9909 2.8111145710879635e-09 26.20398213200438 1.0 0.1201
9910 3.2539725999402652e-09 26.204056286357176 1.0 0.12
9911 3.296344711801157e-09 26.204469858232464 1.0 0.12
9912 3.375739022436282e-09 26.204214955181286 1.0 0.12
9913 3.635441876115849e-09 26.204683990209656 1.0 0.1198
9914 3.1407166609505896e-09 26.204740143130813 1.0 0.1199
9915 3.4533581613697592e-09 26.204478426094518 1.0 0.1199
9916 2.832707032397277e-09 26.205353675270214 1.0 0.1199
9917 3.4793110377169647e-09 26.20544235621713 1.0 0.1201
9918 3.3591443656843364e-09 26.205163915649184

In [11]:
dd_y=pd.DataFrame(data=y_train_cat)
y_train=pd.get_dummies(dd_y,columns = list(dd_y.columns)).to_numpy().astype(dtype=float);

dd_y=pd.DataFrame(data=y_test_cat)
y_test=pd.get_dummies(dd_y,columns = list(dd_y.columns)).to_numpy().astype(dtype=float);


# split the dataset
permutation = np.random.permutation(x_train.shape[0]);
x_train=x_train[permutation,:]
y_train=y_train[permutation,:]

# small subset:
subset_size = 100;
x_train=x_train[:subset_size,:]
y_train=y_train[:subset_size,:]


n_train=x_train.shape[0];

# create tensor variables for data, we do not need gradient w.r.t. to them
t_x_test=torch.tensor(x_test,requires_grad=False,device=device);
t_y_test=torch.tensor(y_test,requires_grad=False,device=device);

In [12]:
#define starting value of weights W for gradient descent
init_std_dev = 0.01;
initialW=init_std_dev*np.random.randn(n_features,n_classes)
# create a PyTorch tensor variable for W and b. 
# we will be optimizing over W, b, finding their best value using gradient descent,
#so we need gradient enabled
W = torch.tensor(initialW,requires_grad=True,device=device);
b = torch.zeros((1,n_classes),requires_grad=True,device=device);
# this optimizer will do gradient descent for us
learning_rate = 0.0001;
#optimizer = torch.optim.SGD([W,b],lr=learning_rate)
optimizer = torch.optim.Adam([W,b],lr=learning_rate)
n_epochs = 10000;
batch_size = 64;


In [13]:
for i in range(n_epochs):

    
    permutation = np.random.permutation(x_train.shape[0]);
    x_train=x_train[permutation,:]
    y_train=y_train[permutation,:]

    accuracy = 0.0;

    #looping over batch_size
    for j in range(0,n_train,batch_size):
        t_x_train = torch.tensor(x_train[j:j+batch_size,:],requires_grad=False,device=device);
        t_y_train = torch.tensor(y_train[j:j+batch_size,:],requires_grad=False,device=device);

        # clear previous gradient calculations
        optimizer.zero_grad();
        
        # calculate model predictions
        linear_predictions = torch.matmul(t_x_train,W)+b
        activations =  torch.exp(linear_predictions);
    
        #Passing through softmax
        sum_activations = torch.sum(activations,dim=1,keepdim=True)
        normalized_activations = torch.div(activations, sum_activations);
        cross_entropy_loss = torch.sum(torch.multiply(t_y_train,torch.log(normalized_activations)),dim=1 )
        risk = -1.0 * torch.mean(cross_entropy_loss );

        # calculate gradients
        risk.backward();
        
        # take the gradient step
        optimizer.step();
        

        batch_risk=risk.item();

        true_class = np.argmax(t_y_train.detach().cpu().numpy(),axis=1)
        pred_class = np.argmax(normalized_activations.detach().cpu().numpy(),axis=1)
        accuracy += np.count_nonzero(true_class == pred_class);
        
    # calculate test set risk and accuracy
    #  turn off gradeints 
        
    with (torch.no_grad()):
      linear_predictions = torch.matmul(t_x_test,W)+b
      activations =  torch.exp(linear_predictions);
    
      #Passing through softmax
      sum_activations = torch.sum(activations,dim=1,keepdim=True)
      test_normalized_activations = torch.div(activations, sum_activations);
      cross_entropy_loss = torch.sum(torch.multiply(t_y_test,torch.log(test_normalized_activations)),dim=1 )
    
      test_risk = -1.0 * torch.mean(cross_entropy_loss );
    
      test_true_class = np.argmax(t_y_test.detach().cpu().numpy(),axis=1)
      test_pred_class = np.argmax(test_normalized_activations.detach().cpu().numpy(),axis=1)
      test_accuracy = np.count_nonzero(test_true_class == test_pred_class)/test_pred_class.shape[0];
      test_error = 1.0 - test_accuracy;
        
    accuracy = accuracy / float(x_train.shape[0])
    print(i,batch_risk,test_risk.item(),accuracy,test_accuracy)

0 2.3058597580047966 2.3037891497203757 0.08 0.0751
1 2.30193195043714 2.30417246840202 0.08 0.073
2 2.284186036202041 2.304669694761212 0.08 0.068
3 2.281777253319606 2.3052317299422342 0.08 0.0638
4 2.2893495989886747 2.305758859985482 0.08 0.0625
5 2.28828267077663 2.3064715754512144 0.11 0.0622
6 2.286586238519642 2.3072241396696636 0.12 0.0608
7 2.2689045796230554 2.3079790202522634 0.15 0.0585
8 2.2628993655739285 2.308761143044996 0.19 0.0614
9 2.2552250257134254 2.309624789072715 0.18 0.0621
10 2.2602866578687677 2.3106291500368825 0.2 0.0642
11 2.268892963142193 2.3116235401876257 0.22 0.0654
12 2.2740166976685234 2.3127126687547377 0.25 0.0669
13 2.257461712333102 2.3138149772956464 0.28 0.0686
14 2.251206780142625 2.3149392912236095 0.28 0.0698
15 2.2407374798482014 2.316079490426536 0.28 0.0708
16 2.2532026618318004 2.317282586778558 0.28 0.0713
17 2.2088868060106837 2.318482793861204 0.26 0.0718
18 2.2398700008218397 2.319771747880765 0.27 0.0735
19 2.2046133762451414 2.32

160 1.816898372520765 2.428427473830645 0.59 0.1272
161 1.8029925689079218 2.428935347732588 0.59 0.1272
162 1.7439623666061093 2.429326688239068 0.59 0.1272
163 1.782655693779289 2.4297244569280423 0.59 0.1268
164 1.8394068409942907 2.4301050206670145 0.59 0.1264
165 1.6843700337607974 2.4303837880218673 0.59 0.127
166 1.7445689376086209 2.4307428515029073 0.6 0.1273
167 1.7487530214155302 2.431088598841305 0.61 0.1275
168 1.7004739146854588 2.431396475148894 0.61 0.1274
169 1.6722487396212835 2.4317953166591466 0.61 0.1276
170 1.7908490399136794 2.432204781762152 0.61 0.1277
171 1.6524940075424948 2.4325514995387945 0.61 0.1279
172 1.7336806528593505 2.4330019230147837 0.61 0.1281
173 1.726679929792601 2.4333842119136664 0.61 0.1281
174 1.759795848256169 2.4337148664754333 0.61 0.1281
175 1.738611137042439 2.4341008893878806 0.61 0.1281
176 1.64723268808552 2.4344933020391064 0.61 0.1284
177 1.7590789721934454 2.435058072218026 0.61 0.1291
178 1.636041101504465 2.435513263187042 0.61

321 1.4559626104143373 2.5022927899382097 0.71 0.1362
322 1.4174982251554051 2.5029188425291133 0.71 0.1362
323 1.3305550015292218 2.5035056327126397 0.71 0.1365
324 1.4044659237786572 2.50415264706295 0.71 0.1366
325 1.4537365428829878 2.5047652826716833 0.71 0.1368
326 1.3900511750765108 2.5052518488208095 0.71 0.1368
327 1.4232049662919988 2.505769894734364 0.71 0.1367
328 1.3750132129616068 2.506368942738696 0.71 0.137
329 1.462334970451852 2.5069439287409905 0.72 0.1369
330 1.397393751101079 2.507435289567225 0.72 0.1369
331 1.4367220739752762 2.508166084831633 0.72 0.1367
332 1.4297842205186635 2.5088487367364296 0.72 0.1365
333 1.4226071617777238 2.509417384137154 0.72 0.1367
334 1.463461649467113 2.509999930053423 0.72 0.1367
335 1.3943953017634731 2.5104554797661245 0.73 0.1368
336 1.3540918014141847 2.510976273440533 0.73 0.1371
337 1.2799752226852328 2.5116379730541887 0.73 0.1372
338 1.3696019049517478 2.5122358572257655 0.73 0.1373
339 1.2542975402951784 2.512785300588277 

479 1.0839668872962167 2.5896903280391985 0.85 0.1423
480 1.1111810518557723 2.5903316126231926 0.85 0.1424
481 1.142522793486445 2.5909919640594925 0.85 0.1425
482 1.0509058580219544 2.591640093612803 0.85 0.1425
483 1.0776340487113074 2.5923880625871956 0.85 0.1426
484 1.0924995516989848 2.5930952396861904 0.85 0.1427
485 1.107214639739669 2.5937864752585424 0.85 0.1426
486 1.0776440564188827 2.594492048978849 0.85 0.1425
487 1.1055977881074648 2.5952060469453406 0.85 0.1425
488 1.0473339112141946 2.595989669778285 0.85 0.1426
489 1.0327546577445166 2.59659220052041 0.85 0.1425
490 1.219689192408889 2.597136119601018 0.85 0.1428
491 1.1920473319673701 2.597782424277454 0.85 0.1431
492 1.176803194122196 2.5982267153276113 0.85 0.1431
493 1.116203995280374 2.59853267746267 0.85 0.1432
494 0.97467365034393 2.5987925212105933 0.85 0.143
495 1.1226888561459936 2.5990948535084684 0.86 0.1429
496 1.1382139071951807 2.5994394589218492 0.86 0.1429
497 1.0742802514338519 2.6000643386720266 0.8

643 1.0487657868287825 2.689322693417669 0.89 0.1479
644 0.921706642015087 2.689966938320078 0.89 0.1481
645 0.9483641964960507 2.6905497382791452 0.89 0.1481
646 0.9202219162337825 2.6911307339566055 0.89 0.1481
647 0.8723389469890955 2.6916899199414535 0.89 0.148
648 0.965098158704293 2.692306118844241 0.89 0.1481
649 0.902853050273063 2.6929275777252557 0.89 0.1479
650 0.9495826075163356 2.6934634195052727 0.89 0.1481
651 0.8993700721493229 2.693931954534275 0.89 0.148
652 0.9562733770331204 2.694415049386196 0.89 0.1481
653 0.9589343877994254 2.6948885914072425 0.89 0.1482
654 0.9388823269299821 2.695517409209924 0.89 0.1483
655 0.908638249575996 2.6959686754376593 0.89 0.1485
656 0.891102841605751 2.6963856492195806 0.89 0.1488
657 0.879645461377843 2.696889112104993 0.89 0.1489
658 0.9523076817561404 2.697314475876383 0.89 0.1488
659 1.0305100519496748 2.697701042489822 0.89 0.1488
660 0.9196910130646718 2.6981645735177144 0.89 0.1489
661 1.0061678575189765 2.698768179764733 0.89

...

9314 0.001016668965316326 7.411444607726375 1.0 0.1489
9315 0.0011329960669708655 7.411929461732729 1.0 0.1489
9316 0.0009675250242057986 7.412408207581945 1.0 0.1489
9317 0.000934370596942579 7.4129380384121575 1.0 0.1489
9318 0.000937722736599911 7.413507396879829 1.0 0.149
9319 0.0008377329063253219 7.41404306683047 1.0 0.1491
9320 0.0009763029620305608 7.414535783387514 1.0 0.1491
9321 0.0009572994314792321 7.415051803506845 1.0 0.1491
9322 0.0007682195167063863 7.415631563804331 1.0 0.1491
9323 0.0008636620716013012 7.4162121480589995 1.0 0.1491
9324 0.0012009007622209948 7.4167215394867325 1.0 0.1491
9325 0.0010092039315645332 7.417225400086745 1.0 0.1491
9326 0.0010898338721014324 7.417735799139902 1.0 0.1491
9327 0.00117678696086143 7.4182201888382115 1.0 0.1491
9328 0.0009278527088399219 7.418768409317831 1.0 0.1491
9329 0.0011009109987261403 7.419204223254923 1.0 0.1491
9330 0.000946045633863952 7.419654739912314 1.0 0.1491
9331 0.0011512185012072032 7.420143651569527 1.0 0.1

9466 0.0008592722541530703 7.495024580530761 1.0 0.1493
9467 0.0007794775174573286 7.495682481296026 1.0 0.1493
9468 0.0010673796266462716 7.496358426029223 1.0 0.1492
9469 0.0008859648050694107 7.496985059328658 1.0 0.1492
9470 0.0007924747244478112 7.497589990189155 1.0 0.1492
9471 0.0008652545097394784 7.498276427050016 1.0 0.1492
9472 0.0009794200829055175 7.4989512037808685 1.0 0.1493
9473 0.0009158401020424802 7.499733693097587 1.0 0.1493
9474 0.0006530831805384265 7.500387106898468 1.0 0.1493
9475 0.0009708575501394175 7.500923347804994 1.0 0.1493
9476 0.0007898873546646582 7.50142910850002 1.0 0.1493
9477 0.0006851459114192462 7.5020744910057 1.0 0.1493
9478 0.000699378379366089 7.502612687765181 1.0 0.1493
9479 0.0009752571220677747 7.503094391598574 1.0 0.1493
9480 0.0008578014958643881 7.503619013982557 1.0 0.1493
9481 0.0009548018277165289 7.504176651586231 1.0 0.1493
9482 0.0007311681982619846 7.504683663328612 1.0 0.1493
9483 0.0008885624972898881 7.505090870625175 1.0 0.

9617 0.0006862556673259559 7.579991648355861 1.0 0.1491
9618 0.0007529340580547302 7.58049351793075 1.0 0.1491
9619 0.0006472954099609656 7.580984100840797 1.0 0.1491
9620 0.0006954663794738829 7.581578762658508 1.0 0.1491
9621 0.0006795870363715867 7.58213216093191 1.0 0.149
9622 0.0009550618021149965 7.582626058722687 1.0 0.149
9623 0.0008270519156818052 7.583172044322919 1.0 0.149
9624 0.0006156529522745971 7.583693060690328 1.0 0.149
9625 0.0007077988476990699 7.584230008436642 1.0 0.149
9626 0.0008614732843668935 7.584875656381504 1.0 0.149
9627 0.0006222258777109291 7.585419281380565 1.0 0.149
9628 0.0005632794915333183 7.5859689580810965 1.0 0.1489
9629 0.0008398158993584875 7.586463175184345 1.0 0.1489
9630 0.0007263200712811328 7.5868952712329545 1.0 0.1489
9631 0.000857241691971201 7.587425111119491 1.0 0.1489
9632 0.0007973746720372076 7.588021112404796 1.0 0.1489
9633 0.000969398373751484 7.588547384024142 1.0 0.1489
9634 0.0007672080979418427 7.589041666086755 1.0 0.1489
9

9770 0.0007655071577727818 7.66835222082572 1.0 0.149
9771 0.0006111690566457142 7.668927412496092 1.0 0.1491
9772 0.0008022668904160506 7.669428823931736 1.0 0.1491
9773 0.000807216399859195 7.669916652532935 1.0 0.1491
9774 0.0007559901660647942 7.670451918460246 1.0 0.1491
9775 0.0006790230224334662 7.670884197110308 1.0 0.1491
9776 0.000725431870349162 7.67127558798914 1.0 0.149
9777 0.0006560583563406504 7.671748120670798 1.0 0.1489
9778 0.0006035508786403848 7.6720801778960395 1.0 0.1489
9779 0.0008602064505828433 7.672464712510031 1.0 0.1488
9780 0.0006893975956338478 7.672854361624176 1.0 0.1487
9781 0.0006851374733661633 7.673297232571614 1.0 0.1487
9782 0.000661804395547159 7.673908260816568 1.0 0.1487
9783 0.0008101736218453916 7.67455774964738 1.0 0.1487
9784 0.0006648587707007085 7.6751706505763515 1.0 0.1487
9785 0.0007329545034421383 7.675765549991057 1.0 0.1487
9786 0.0005390093527080785 7.676328122766264 1.0 0.1487
9787 0.0006242662373585105 7.676789165856484 1.0 0.148

9925 0.0004261127309624126 7.753009296157633 1.0 0.149
9926 0.0004555915976621251 7.753627024123112 1.0 0.149
9927 0.0005278290184596275 7.754208191121472 1.0 0.1491
9928 0.0006648279264902444 7.754749505472004 1.0 0.1491
9929 0.0006415704811350731 7.755327675231869 1.0 0.1491
9930 0.0007909715021473853 7.755957591392737 1.0 0.1491
9931 0.0005595522876425074 7.756627454164172 1.0 0.1491
9932 0.0005305250136344731 7.757145555923612 1.0 0.1491
9933 0.0006023178090241517 7.757779162831107 1.0 0.1491
9934 0.0006747573109448429 7.75834438986376 1.0 0.149
9935 0.0005265368885087039 7.758931471147222 1.0 0.149
9936 0.0006980673146066256 7.759488688967166 1.0 0.149
9937 0.0004936388849155336 7.7600103746732465 1.0 0.149
9938 0.000576971551153217 7.760642702755342 1.0 0.149
9939 0.0007605526855205616 7.761221678128282 1.0 0.149
9940 0.0005871202066191325 7.76178002899296 1.0 0.149
9941 0.0006551627056988046 7.76243473530183 1.0 0.149
9942 0.0006588901880437156 7.763093048762048 1.0 0.149
9943 0

In [14]:
dd_y=pd.DataFrame(data=y_train_cat)
y_train=pd.get_dummies(dd_y,columns = list(dd_y.columns)).to_numpy().astype(dtype=float);

dd_y=pd.DataFrame(data=y_test_cat)
y_test=pd.get_dummies(dd_y,columns = list(dd_y.columns)).to_numpy().astype(dtype=float);


# split the dataset
permutation = np.random.permutation(x_train.shape[0]);
x_train=x_train[permutation,:]
y_train=y_train[permutation,:]

# small subset:
subset_size = 2000;
x_train=x_train[:subset_size,:]
y_train=y_train[:subset_size,:]


n_train=x_train.shape[0];

# create tensor variables for data, we do not need gradient w.r.t. to them
t_x_test=torch.tensor(x_test,requires_grad=False,device=device);
t_y_test=torch.tensor(y_test,requires_grad=False,device=device);

In [15]:
#define starting value of weights W for gradient descent
init_std_dev = 0.01;
initialW=init_std_dev*np.random.randn(n_features,n_classes)
# create a PyTorch tensor variable for W and b. 
# we will be optimizing over W, b, finding their best value using gradient descent,
#so we need gradient enabled
W = torch.tensor(initialW,requires_grad=True,device=device);
b = torch.zeros((1,n_classes),requires_grad=True,device=device);
# this optimizer will do gradient descent for us
learning_rate = 0.1;
#optimizer = torch.optim.SGD([W,b],lr=learning_rate)
optimizer = torch.optim.Adam([W,b],lr=learning_rate)
n_epochs = 10000;
batch_size = 64;


In [16]:
for i in range(n_epochs):

    
    permutation = np.random.permutation(x_train.shape[0]);
    x_train=x_train[permutation,:]
    y_train=y_train[permutation,:]

    accuracy = 0.0;

    #looping over batch_size
    for j in range(0,n_train,batch_size):
        t_x_train = torch.tensor(x_train[j:j+batch_size,:],requires_grad=False,device=device);
        t_y_train = torch.tensor(y_train[j:j+batch_size,:],requires_grad=False,device=device);

        # clear previous gradient calculations
        optimizer.zero_grad();
        
        # calculate model predictions
        linear_predictions = torch.matmul(t_x_train,W)+b
        activations =  torch.exp(linear_predictions);
    
        #Passing through softmax
        sum_activations = torch.sum(activations,dim=1,keepdim=True)
        normalized_activations = torch.div(activations, sum_activations);
        cross_entropy_loss = torch.sum(torch.multiply(t_y_train,torch.log(normalized_activations)),dim=1 )
        risk = -1.0 * torch.mean(cross_entropy_loss );

        # calculate gradients
        risk.backward();
        
        # take the gradient step
        optimizer.step();
        

        batch_risk=risk.item();

        true_class = np.argmax(t_y_train.detach().cpu().numpy(),axis=1)
        pred_class = np.argmax(normalized_activations.detach().cpu().numpy(),axis=1)
        accuracy += np.count_nonzero(true_class == pred_class);
        
    # calculate test set risk and accuracy
    #  turn off gradeints 
        
    with (torch.no_grad()):
      linear_predictions = torch.matmul(t_x_test,W)+b
      activations =  torch.exp(linear_predictions);
    
      #Passing through softmax
      sum_activations = torch.sum(activations,dim=1,keepdim=True)
      test_normalized_activations = torch.div(activations, sum_activations);
      cross_entropy_loss = torch.sum(torch.multiply(t_y_test,torch.log(test_normalized_activations)),dim=1 )
    
      test_risk = -1.0 * torch.mean(cross_entropy_loss );
    
      test_true_class = np.argmax(t_y_test.detach().cpu().numpy(),axis=1)
      test_pred_class = np.argmax(test_normalized_activations.detach().cpu().numpy(),axis=1)
      test_accuracy = np.count_nonzero(test_true_class == test_pred_class)/test_pred_class.shape[0];
      test_error = 1.0 - test_accuracy;
        
    accuracy = accuracy / float(x_train.shape[0])
    print(i,batch_risk,test_risk.item(),accuracy,test_accuracy)

0 6.922710098770267 7.811875294181208 0.12 0.111
1 3.2036134267261653 7.850370994268208 0.4 0.066
2 2.3287786786299924 7.261006279943115 0.49 0.0755
3 0.9704103268943 7.059017580254574 0.78 0.131
4 1.0373830068829184 8.063904895848426 0.76 0.1241
5 0.6807718446480853 8.534888229335854 0.82 0.1527
6 0.25785233375283084 8.538341244675156 0.88 0.1494
7 0.28926310322377735 8.778835561093324 0.91 0.1201
8 0.21466705705609787 9.108724634873719 0.93 0.098
9 0.12432004260818341 9.69441635681242 0.97 0.091
10 0.08069427402774515 10.059710587757634 0.96 0.0925
11 0.050261930237138215 10.178624283018289 0.98 0.1008
12 0.0779272104615207 10.256536588629857 0.98 0.1064
13 0.009446734096663977 10.342123888270537 1.0 0.112
14 0.012028587003856707 10.472382739981413 1.0 0.1148
15 0.03380425702299795 10.586791381701497 1.0 0.1147
16 0.023798879635745545 10.650645438671283 1.0 0.113
17 0.015428644195727481 10.696786329864262 1.0 0.1125
18 0.007732594689082068 10.735746704797485 1.0 0.111
19 0.0099817435

155 0.00034041869124234087 11.164831883979064 1.0 0.1064
156 0.0003722527937378191 11.165003520055036 1.0 0.1066
157 0.0005057893162796162 11.165125199971579 1.0 0.1065
158 0.0003844076866899872 11.165137394454767 1.0 0.1064
159 0.00034779094278781315 11.165389123330264 1.0 0.1063
160 0.0004427525602590329 11.165593428545405 1.0 0.1064
161 0.00036252768322608955 11.166136124135665 1.0 0.1065
162 0.0003548379745060372 11.166685082572938 1.0 0.1064
163 0.0002273186575310176 11.16754508289744 1.0 0.1066
164 0.0004030313970834284 11.168687829779971 1.0 0.1065
165 0.0004522603035960777 11.169970323093454 1.0 0.1065
166 0.0003407378974862167 11.17140237918254 1.0 0.1065
167 0.0005169568059718067 11.172452547557324 1.0 0.1065
168 0.0003744588949494484 11.173639261275367 1.0 0.1065
169 0.00034486993578934405 11.174953406212385 1.0 0.1065
170 0.000351477417603323 11.176395242536213 1.0 0.1065
171 0.00026054264260818487 11.177508271407401 1.0 0.1065
172 0.0002988874328919666 11.178424115013012 1

301 0.0001549397266246668 11.24240140918666 1.0 0.1086
302 0.00022511867714692247 11.242821425351963 1.0 0.1086
303 0.00023376686142978465 11.243246494965636 1.0 0.1086
304 0.00021499569196733437 11.243061277036835 1.0 0.1086
305 0.00019999436038220078 11.243404604839004 1.0 0.1086
306 0.0001680648657447091 11.243599799999702 1.0 0.1087
307 0.00018397466745084763 11.243725183059365 1.0 0.1086
308 0.00020657154930764973 11.243719545458056 1.0 0.1085
309 0.00019298697858698588 11.243745775829852 1.0 0.1086
310 0.00018304385471576242 11.243653999920486 1.0 0.1086
311 0.0002101724706801328 11.243726417437749 1.0 0.1087
312 0.00018067110894259865 11.243930479163843 1.0 0.1086
313 0.00019157152501548776 11.244171847271069 1.0 0.1086
314 0.00020039481651413797 11.244448024518729 1.0 0.1085
315 0.0001850645649289317 11.244854445055061 1.0 0.1085
316 0.00024697432850433003 11.245463585831343 1.0 0.1086
317 0.00016565220282100215 11.246045681862055 1.0 0.1086
318 0.00018985943395046024 11.246969

449 0.00010634465695929009 11.310011103691904 1.0 0.1113
450 0.00011853136998246381 11.310588622364902 1.0 0.1113
451 9.152405678802372e-05 11.311260994202593 1.0 0.1113
452 0.00010368583688000346 11.311586465579397 1.0 0.1114
453 0.00010745530353464265 11.312006389795174 1.0 0.1114
454 9.844457811799143e-05 11.312410763394414 1.0 0.1114
455 0.00013145765981595033 11.312811427799916 1.0 0.1114
456 0.00012559655106776112 11.313070295446627 1.0 0.1114
457 0.0001225560820994239 11.313196718987625 1.0 0.1116
458 0.00011085732903373813 11.313420372758301 1.0 0.1116
459 0.00011457298862135291 11.313619333810358 1.0 0.1117
460 0.000145959527197591 11.313864738444725 1.0 0.1115
461 9.872909635165864e-05 11.314384280282967 1.0 0.1115
462 0.00011940409283244802 11.314815137349049 1.0 0.1115
463 9.376740599856468e-05 11.31539095880134 1.0 0.1114
464 0.000138281926225517 11.316063095554945 1.0 0.1114
465 9.008686669203662e-05 11.316800466243006 1.0 0.1114
466 0.00013235518509774295 11.317542338170

603 7.783487409270871e-05 11.379434861162393 1.0 0.112
604 7.667303490982071e-05 11.380070829393253 1.0 0.112
605 6.637738447472817e-05 11.38052171693325 1.0 0.112
606 7.927475143160646e-05 11.380955164631846 1.0 0.112
607 4.5827698980938397e-05 11.381413983968985 1.0 0.112
608 8.104577016882536e-05 11.381929142466268 1.0 0.112
609 9.634999766800115e-05 11.38254321278613 1.0 0.1122
610 7.950642040037405e-05 11.383336465231622 1.0 0.1122
611 7.388063913942234e-05 11.38412692850424 1.0 0.1122
612 7.221104068836178e-05 11.384766713330452 1.0 0.1122
613 6.159765325820635e-05 11.385351674656965 1.0 0.1123
614 9.544242773080646e-05 11.38591840483159 1.0 0.1122
615 6.592441334264722e-05 11.386227204353489 1.0 0.1121
616 8.861498181942528e-05 11.386714187408357 1.0 0.1121
617 8.485931366796551e-05 11.387170408701044 1.0 0.1121
618 6.730797819897202e-05 11.387449354478779 1.0 0.1121
619 9.095900549289231e-05 11.387648993968847 1.0 0.1121
620 9.181268242598248e-05 11.388095230877664 1.0 0.1121
6

...

9330 6.0449391495862965e-09 15.732306629195506 1.0 0.1125
9331 6.993210751839404e-09 15.732873921076825 1.0 0.1124
9332 5.204426219249302e-09 15.733513975759815 1.0 0.1124
9333 7.26849830768667e-09 15.734138758292614 1.0 0.1124
9334 6.504040645043563e-09 15.734817862695973 1.0 0.1124
9335 7.74311918528619e-09 15.735471272076934 1.0 0.1124
9336 6.689080578500524e-09 15.736090239389025 1.0 0.1124
9337 7.054269156660588e-09 15.736664673144015 1.0 0.1124
9338 7.176788912290479e-09 15.737285787374088 1.0 0.1123
9339 6.695435960076746e-09 15.73783588518911 1.0 0.1124
9340 6.7870853758943445e-09 15.738408723849817 1.0 0.1123
9341 6.027805994933569e-09 15.739026368757692 1.0 0.1124
9342 7.306352480247058e-09 15.73972886842466 1.0 0.1124
9343 5.90741486022118e-09 15.740306298979855 1.0 0.1123
9344 6.550157397779602e-09 15.740976630053117 1.0 0.1124
9345 7.569612783260938e-09 15.741648731160018 1.0 0.1124
9346 9.037370848471804e-09 15.742335389569536 1.0 0.1124
9347 7.430659365749094e-09 15.7430

9478 6.758458198197857e-09 15.812331625217281 1.0 0.1125
9479 5.2752739603953266e-09 15.81284861419741 1.0 0.1125
9480 5.3817961220472495e-09 15.813399394048698 1.0 0.1125
9481 5.888730778556803e-09 15.81391540848403 1.0 0.1126
9482 6.8078878136214365e-09 15.814474113638253 1.0 0.1126
9483 6.232389975360734e-09 15.815002954998404 1.0 0.1126
9484 5.384075540711107e-09 15.81567787548641 1.0 0.1126
9485 6.501913354899161e-09 15.81636014657865 1.0 0.1126
9486 5.782087755765295e-09 15.817004595722072 1.0 0.1126
9487 5.138757867147153e-09 15.817613040226433 1.0 0.1126
9488 6.832297861700344e-09 15.818131048411626 1.0 0.1126
9489 5.5850018783165875e-09 15.818729317253036 1.0 0.1126
9490 5.09504799772489e-09 15.81933874867122 1.0 0.1126
9491 5.518956147385628e-09 15.819876495917542 1.0 0.1126
9492 4.72874507834316e-09 15.820416449275097 1.0 0.1126
9493 4.993352334227905e-09 15.820976995615545 1.0 0.1126
9494 6.027578394518651e-09 15.821576191133886 1.0 0.1126
9495 6.134600016655864e-09 15.8221

9623 5.011109722062898e-09 15.895235153533932 1.0 0.1121
9624 5.971868333155173e-09 15.895935920408741 1.0 0.1121
9625 4.949891811779793e-09 15.896599581504036 1.0 0.1121
9626 4.667250513675444e-09 15.89715002725863 1.0 0.1122
9627 5.018668908016073e-09 15.897632720203008 1.0 0.1122
9628 6.124122932306951e-09 15.898092165818642 1.0 0.1122
9629 4.063640798672356e-09 15.898517766743712 1.0 0.1122
9630 5.089264279100649e-09 15.898944001039682 1.0 0.1122
9631 4.964878426545578e-09 15.899391015827987 1.0 0.1122
9632 4.252453802288103e-09 15.899801412769227 1.0 0.1122
9633 5.6268509613617e-09 15.90026601898445 1.0 0.1122
9634 5.147030004725412e-09 15.90080524354464 1.0 0.1122
9635 5.2712297286405895e-09 15.901365639975554 1.0 0.1122
9636 4.946846398936514e-09 15.90195987976658 1.0 0.1122
9637 5.5642242176381274e-09 15.902576292386453 1.0 0.1122
9638 5.073593379793681e-09 15.903187233801313 1.0 0.1122
9639 5.088050980355976e-09 15.903793255516193 1.0 0.1122
9640 4.635275573007244e-09 15.90441

9770 4.725574133747477e-09 15.978543641683244 1.0 0.1122
9771 4.385995978258801e-09 15.978990259495177 1.0 0.1122
9772 4.495827208620774e-09 15.979376060898453 1.0 0.1122
9773 5.01463649677035e-09 15.979781354923293 1.0 0.1122
9774 5.30555254414806e-09 15.980225999447208 1.0 0.1122
9775 4.228967690442152e-09 15.98070677181099 1.0 0.1122
9776 4.6552835262745885e-09 15.98118077817023 1.0 0.1122
9777 4.538810740723067e-09 15.981726026388019 1.0 0.1122
9778 4.876193017462549e-09 15.982271218157809 1.0 0.1123
9779 4.979634536842568e-09 15.982816428298847 1.0 0.1123
9780 4.304491690580934e-09 15.983307636630553 1.0 0.1123
9781 4.493406207875152e-09 15.983806195727057 1.0 0.1123
9782 4.0963673294127116e-09 15.984363444673459 1.0 0.1123
9783 4.441200535629619e-09 15.984820055526873 1.0 0.1123
9784 4.05162450664794e-09 15.985251719508629 1.0 0.1122
9785 4.961920824544615e-09 15.985696140302641 1.0 0.1122
9786 4.28113452661379e-09 15.986247649377514 1.0 0.1122
9787 4.807061539125023e-09 15.98674

9919 4.364083501910481e-09 16.057997818895462 1.0 0.1125
9920 3.893250068820999e-09 16.05865517484186 1.0 0.1125
9921 3.227417187575339e-09 16.05929508853569 1.0 0.1125
9922 3.846443762690286e-09 16.059890218281733 1.0 0.1125
9923 3.212945430351506e-09 16.060502779830998 1.0 0.1125
9924 4.2406877482111205e-09 16.06103373010245 1.0 0.1124
9925 4.804266436561955e-09 16.061495889859437 1.0 0.1124
9926 3.85224334916494e-09 16.062057320758775 1.0 0.1123
9927 3.5998189625877386e-09 16.062573709450387 1.0 0.1123
9928 4.161071434278334e-09 16.06311749329357 1.0 0.1123
9929 4.046794270768881e-09 16.063645050303034 1.0 0.1123
9930 3.1159797425563842e-09 16.064264684639557 1.0 0.1123
9931 3.755296711494598e-09 16.064881988433754 1.0 0.1123
9932 4.271574872440568e-09 16.065457329228163 1.0 0.1123
9933 4.460125251113189e-09 16.06591430768509 1.0 0.1123
9934 4.239062119216865e-09 16.06642113115779 1.0 0.1123
9935 4.751957946582493e-09 16.0669198506612 1.0 0.1123
9936 4.2444242072997e-09 16.067432284

In [17]:
dd_y=pd.DataFrame(data=y_train_cat)
y_train=pd.get_dummies(dd_y,columns = list(dd_y.columns)).to_numpy().astype(dtype=float);

dd_y=pd.DataFrame(data=y_test_cat)
y_test=pd.get_dummies(dd_y,columns = list(dd_y.columns)).to_numpy().astype(dtype=float);


# split the dataset
permutation = np.random.permutation(x_train.shape[0]);
x_train=x_train[permutation,:]
y_train=y_train[permutation,:]

# small subset:
subset_size = 2000;
x_train=x_train[:subset_size,:]
y_train=y_train[:subset_size,:]


n_train=x_train.shape[0];

# create tensor variables for data, we do not need gradient w.r.t. to them
t_x_test=torch.tensor(x_test,requires_grad=False,device=device);
t_y_test=torch.tensor(y_test,requires_grad=False,device=device);

#define starting value of weights W for gradient descent
init_std_dev = 0.01;
initialW=init_std_dev*np.random.randn(n_features,n_classes)
# create a PyTorch tensor variable for W and b. 
# we will be optimizing over W, b, finding their best value using gradient descent,
#so we need gradient enabled
W = torch.tensor(initialW,requires_grad=True,device=device);
b = torch.zeros((1,n_classes),requires_grad=True,device=device);
# this optimizer will do gradient descent for us
learning_rate = 0.001;
#optimizer = torch.optim.SGD([W,b],lr=learning_rate)
optimizer = torch.optim.Adam([W,b],lr=learning_rate)
n_epochs = 10000;
batch_size = 64;

for i in range(n_epochs):

    
    permutation = np.random.permutation(x_train.shape[0]);
    x_train=x_train[permutation,:]
    y_train=y_train[permutation,:]

    accuracy = 0.0;

    #looping over batch_size
    for j in range(0,n_train,batch_size):
        t_x_train = torch.tensor(x_train[j:j+batch_size,:],requires_grad=False,device=device);
        t_y_train = torch.tensor(y_train[j:j+batch_size,:],requires_grad=False,device=device);

        # clear previous gradient calculations
        optimizer.zero_grad();
        
        # calculate model predictions
        linear_predictions = torch.matmul(t_x_train,W)+b
        activations =  torch.exp(linear_predictions);
    
        #Passing through softmax
        sum_activations = torch.sum(activations,dim=1,keepdim=True)
        normalized_activations = torch.div(activations, sum_activations);
        cross_entropy_loss = torch.sum(torch.multiply(t_y_train,torch.log(normalized_activations)),dim=1 )
        risk = -1.0 * torch.mean(cross_entropy_loss );

        # calculate gradients
        risk.backward();
        
        # take the gradient step
        optimizer.step();
        

        batch_risk=risk.item();

        true_class = np.argmax(t_y_train.detach().cpu().numpy(),axis=1)
        pred_class = np.argmax(normalized_activations.detach().cpu().numpy(),axis=1)
        accuracy += np.count_nonzero(true_class == pred_class);
        
    # calculate test set risk and accuracy
    #  turn off gradeints 
        
    with (torch.no_grad()):
      linear_predictions = torch.matmul(t_x_test,W)+b
      activations =  torch.exp(linear_predictions);
    
      #Passing through softmax
      sum_activations = torch.sum(activations,dim=1,keepdim=True)
      test_normalized_activations = torch.div(activations, sum_activations);
      cross_entropy_loss = torch.sum(torch.multiply(t_y_test,torch.log(test_normalized_activations)),dim=1 )
    
      test_risk = -1.0 * torch.mean(cross_entropy_loss );
    
      test_true_class = np.argmax(t_y_test.detach().cpu().numpy(),axis=1)
      test_pred_class = np.argmax(test_normalized_activations.detach().cpu().numpy(),axis=1)
      test_accuracy = np.count_nonzero(test_true_class == test_pred_class)/test_pred_class.shape[0];
      test_error = 1.0 - test_accuracy;
        
    accuracy = accuracy / float(x_train.shape[0])
    print(i,batch_risk,test_risk.item(),accuracy,test_accuracy)


0 2.286392079036303 2.312281919501978 0.13 0.0726
1 2.248758489354844 2.3185164765160655 0.19 0.0864
2 2.1791819429961126 2.3268977817557706 0.24 0.0943
3 2.161590775279675 2.336939806340483 0.31 0.0984
4 2.0726376618707274 2.346098284102451 0.33 0.0986
5 2.0948785109042785 2.3535669929238474 0.38 0.1018
6 2.054896312711594 2.3594515243165937 0.39 0.1072
7 1.965783359673821 2.363678698811624 0.43 0.1083
8 1.8788681747213947 2.3686376996439953 0.42 0.1064
9 1.998119486060366 2.3721494239828287 0.44 0.1061
10 1.9044035529392116 2.373929251001626 0.48 0.1022
11 1.9001291117302566 2.374182306192103 0.5 0.1003
12 1.7721459746594443 2.374326336473246 0.56 0.0973
13 1.8589787707818064 2.3749863705355923 0.58 0.092
14 1.7327271555275987 2.3761520255474453 0.6 0.089
15 1.784926260933378 2.378138036688784 0.62 0.0862
16 1.6906716102968535 2.380471570046546 0.66 0.0857
17 1.7013551072132345 2.383158974858567 0.66 0.0858
18 1.606487939863153 2.387159645475784 0.65 0.0868
19 1.647092676671005 2.391

160 0.37318433488154423 3.1200669331244155 0.97 0.1078
161 0.41943733703981123 3.124626843573591 0.97 0.1079
162 0.39642318019890044 3.1284233394614165 0.97 0.1085
163 0.3944212985198432 3.1321035678565665 0.97 0.1085
164 0.3966228810078992 3.1354827044276345 0.97 0.1088
165 0.37939663496010917 3.138093294813996 0.97 0.1085
166 0.3947590409587894 3.139977800743065 0.97 0.1088
167 0.381965689567314 3.1415220504921306 0.97 0.1086
168 0.3510802321068882 3.1433462447381153 0.97 0.1084
169 0.4230854080744007 3.1460069564777324 0.98 0.1083
170 0.4306135029404391 3.1495356866583206 0.98 0.109
171 0.358173141737272 3.1526620063150457 0.98 0.1092
172 0.31717096169496584 3.1562564854636994 0.98 0.1092
173 0.3097772784609222 3.160344262186363 0.98 0.1091
174 0.33193256159632034 3.1645960634060466 0.99 0.1087
175 0.3444810239330804 3.1689154082151525 0.99 0.1093
176 0.32356374655360765 3.1731739503792142 0.99 0.1098
177 0.2826505387076668 3.17789222865996 0.99 0.1098
178 0.4132644364119265 3.18305

316 0.16650566122522029 3.642712539750445 1.0 0.12
317 0.14604183065267595 3.6450826069055715 1.0 0.1201
318 0.18634946953311854 3.647694699416124 1.0 0.12
319 0.13642936347567852 3.6507438547515614 1.0 0.12
320 0.16185722061870392 3.653984784803359 1.0 0.1199
321 0.15533855324575618 3.657254191892395 1.0 0.1203
322 0.15525014909271062 3.6600304156037056 1.0 0.1204
323 0.15106967557295936 3.66262541173339 1.0 0.1202
324 0.14174873509802693 3.6654264664143623 1.0 0.1202
325 0.17501411491644403 3.6684932998205158 1.0 0.1204
326 0.14938976132196957 3.6713898655525887 1.0 0.12
327 0.14297830082363863 3.67468959983432 1.0 0.12
328 0.13920784603975817 3.6776445068260823 1.0 0.1199
329 0.15388240508610196 3.680223497061062 1.0 0.1197
330 0.1560001931583857 3.6826294367295183 1.0 0.1191
331 0.1410052110868343 3.684653220581234 1.0 0.1189
332 0.1858366164507115 3.6876195946911183 1.0 0.1187
333 0.17840764671959494 3.6901396349156195 1.0 0.119
334 0.15504504250402779 3.6927517037204547 1.0 0.119

475 0.09186515312647842 4.022821226574813 1.0 0.1219
476 0.08914122224067761 4.024510433343537 1.0 0.1218
477 0.09449708898187176 4.02637947085998 1.0 0.1222
478 0.09181099830592042 4.02820055842609 1.0 0.1224
479 0.06876988806204504 4.029889139369999 1.0 0.1221
480 0.06292501775108113 4.031560537857993 1.0 0.1221
481 0.09124459445706606 4.033565499810934 1.0 0.1223
482 0.0782992699592736 4.03521929435928 1.0 0.1222
483 0.059194103001536616 4.036974593280056 1.0 0.1223
484 0.07529799737629977 4.038504530481578 1.0 0.1222
485 0.08853483590783855 4.040370576113414 1.0 0.1221
486 0.0807892508787191 4.042087029228342 1.0 0.1218
487 0.06380873807011017 4.044039309230914 1.0 0.1215
488 0.07294284915106942 4.046078293979698 1.0 0.1212
489 0.07586801130038673 4.047977890197366 1.0 0.1213
490 0.05723378555280259 4.0500527416678445 1.0 0.1212
491 0.06724191952623378 4.051988348528529 1.0 0.1213
492 0.08067871351881008 4.053945259519059 1.0 0.1212
493 0.0815592694770809 4.056246314239734 1.0 0.12

636 0.04106133493792647 4.322207625280164 1.0 0.1227
637 0.056988484298357074 4.323693198751334 1.0 0.1224
638 0.055039037220716146 4.325150197750493 1.0 0.1224
639 0.04857434734559078 4.327187837457173 1.0 0.1223
640 0.0439604361036173 4.3294009523502925 1.0 0.1225
641 0.0532485053662209 4.3315826151720875 1.0 0.1223
642 0.046389117283973075 4.333835215266543 1.0 0.1222
643 0.05207660554918354 4.336131063178803 1.0 0.122
644 0.050270180672757354 4.33823100765266 1.0 0.1218
645 0.052681187661853146 4.340416715980558 1.0 0.1219
646 0.059158409641183206 4.342308576188798 1.0 0.1219
647 0.04151770496596689 4.343983465341078 1.0 0.1221
648 0.05449601458185024 4.345788748501276 1.0 0.122
649 0.05196557070427917 4.347547874391303 1.0 0.122
650 0.04379816200766374 4.349328724121393 1.0 0.122
651 0.04644498030693325 4.350857922464148 1.0 0.1223
652 0.039532260081928755 4.3521994634874925 1.0 0.1223
653 0.057537637934127854 4.353436559411829 1.0 0.1224
654 0.04293941240086788 4.354731004295135 

...

9352 2.7205366744633222e-06 10.813263359607419 1.0 0.1168
9353 3.2524012362321364e-06 10.81389633150783 1.0 0.1168
9354 2.614780583804786e-06 10.814547986688828 1.0 0.1168
9355 2.352921540506194e-06 10.815178833004612 1.0 0.1168
9356 2.3624246315093617e-06 10.815795052755762 1.0 0.1168
9357 2.2026329891534858e-06 10.816485418408053 1.0 0.1166
9358 2.513389216921787e-06 10.817157779936434 1.0 0.1166
9359 2.7670525401310635e-06 10.81787713140218 1.0 0.1167
9360 2.937844029387016e-06 10.818704090302358 1.0 0.1168
9361 2.20244473562101e-06 10.819554372221301 1.0 0.1169
9362 3.1861980964025083e-06 10.820364576066172 1.0 0.1169
9363 2.7298654349528376e-06 10.821236810548342 1.0 0.1169
9364 2.7975205278857452e-06 10.822105309136086 1.0 0.1169
9365 2.465835263866024e-06 10.823007165954472 1.0 0.1169
9366 2.9543050540149977e-06 10.823875921710275 1.0 0.1169
9367 2.7056939373537507e-06 10.824834094405244 1.0 0.1169
9368 2.769135448102596e-06 10.825730253995259 1.0 0.1168
9369 2.289954620200014e-

9499 2.6931493011281227e-06 10.914402712335427 1.0 0.117
9500 2.5214938413610507e-06 10.914905137242924 1.0 0.117
9501 2.222198069902428e-06 10.915445008903044 1.0 0.117
9502 2.131951238502236e-06 10.916032984218688 1.0 0.117
9503 1.9287209639449662e-06 10.916674303883465 1.0 0.117
9504 2.0358471569607937e-06 10.917206106971937 1.0 0.117
9505 2.4331679969802532e-06 10.91769195233998 1.0 0.1169
9506 2.2627003254857884e-06 10.918227644387006 1.0 0.117
9507 2.139080074107916e-06 10.918741973771384 1.0 0.117
9508 2.196801443592808e-06 10.91917834796168 1.0 0.117
9509 1.883756991248856e-06 10.91962852940434 1.0 0.1169
9510 2.3626436162742687e-06 10.920077167213396 1.0 0.1169
9511 2.6991698212480524e-06 10.920522798262379 1.0 0.1169
9512 1.8125723110700622e-06 10.921030814148322 1.0 0.1169
9513 2.222483091787112e-06 10.921507147011189 1.0 0.1169
9514 2.4089683619388234e-06 10.922038713247387 1.0 0.1169
9515 2.243293960520033e-06 10.922632191700064 1.0 0.117
9516 2.0954974403599e-06 10.923334

9643 1.6680622333481205e-06 11.008288036670047 1.0 0.117
9644 2.0685436304463727e-06 11.009060652897926 1.0 0.117
9645 2.051513412994313e-06 11.009802550082648 1.0 0.117
9646 1.8616139580690202e-06 11.010569258437748 1.0 0.117
9647 2.1504842152628856e-06 11.011372548486312 1.0 0.117
9648 1.9631434166495547e-06 11.012153494036596 1.0 0.1169
9649 1.9754638274956356e-06 11.013000827564627 1.0 0.1169
9650 1.8372986918256646e-06 11.013845774587907 1.0 0.1169
9651 2.217470155418249e-06 11.0145719285601 1.0 0.1169
9652 2.0181441441813513e-06 11.015131585367868 1.0 0.1169
9653 2.1265745386933357e-06 11.015707940944893 1.0 0.1169
9654 2.153760719623533e-06 11.016418039453901 1.0 0.1169
9655 2.1567323734702562e-06 11.017189688211388 1.0 0.1169
9656 1.915176250571741e-06 11.01790883580409 1.0 0.1169
9657 1.997156141159648e-06 11.018694768751295 1.0 0.1169
9658 2.2449408383506183e-06 11.019471367348768 1.0 0.117
9659 2.091337940249684e-06 11.020180703479904 1.0 0.117
9660 1.8533733222472338e-06 11

9792 1.5714458159351656e-06 11.110578243162497 1.0 0.117
9793 2.17874108943995e-06 11.111208631626086 1.0 0.117
9794 1.8470939288627112e-06 11.11197432904356 1.0 0.117
9795 1.8935056765324716e-06 11.11266830519751 1.0 0.117
9796 1.9639943833255082e-06 11.113378527253532 1.0 0.117
9797 2.0657447080310153e-06 11.113963530385151 1.0 0.117
9798 1.6903182820072891e-06 11.114583319800571 1.0 0.117
9799 1.8737206240934909e-06 11.11523249213339 1.0 0.117
9800 1.4146659465229119e-06 11.115872257011432 1.0 0.1169
9801 1.608331686159777e-06 11.116448548342587 1.0 0.1169
9802 1.7545923546912997e-06 11.117016338655842 1.0 0.117
9803 1.6684546761211322e-06 11.117605574043402 1.0 0.117
9804 1.8480236984882295e-06 11.118271709953527 1.0 0.117
9805 1.5149573621860756e-06 11.119064419391288 1.0 0.117
9806 1.8976355735933218e-06 11.119860819264524 1.0 0.117
9807 1.689069434307253e-06 11.120730099413075 1.0 0.117
9808 1.8219117876951944e-06 11.121404346075739 1.0 0.117
9809 1.5990888760731711e-06 11.12211

9941 1.4141969439734846e-06 11.210811101554112 1.0 0.1169
9942 1.6630442847689375e-06 11.211566456019149 1.0 0.1168
9943 1.5431395835204772e-06 11.212339136392885 1.0 0.1168
9944 1.627683138211611e-06 11.213119180387354 1.0 0.1168
9945 1.6187917667722893e-06 11.21396443448062 1.0 0.1169
9946 1.6055349087405697e-06 11.21486636823807 1.0 0.117
9947 1.5027147603757866e-06 11.21579214802446 1.0 0.117
9948 1.4813718985901988e-06 11.21668935272847 1.0 0.1169
9949 1.5699295770920926e-06 11.21751952699071 1.0 0.1169
9950 1.7499444926719904e-06 11.218353534507687 1.0 0.1169
9951 1.636476097884718e-06 11.219212714203346 1.0 0.117
9952 1.4332847885536635e-06 11.219995329951589 1.0 0.1169
9953 1.6299812563193577e-06 11.220773025607823 1.0 0.1168
9954 1.403592078921369e-06 11.221617190015515 1.0 0.1168
9955 1.578621771160549e-06 11.222198287091208 1.0 0.1167
9956 1.486570829206408e-06 11.222855871088163 1.0 0.1168
9957 1.4899388853854591e-06 11.223383582699855 1.0 0.1168
9958 1.507119665648815e-06 

In [18]:
dd_y=pd.DataFrame(data=y_train_cat)
y_train=pd.get_dummies(dd_y,columns = list(dd_y.columns)).to_numpy().astype(dtype=float);

dd_y=pd.DataFrame(data=y_test_cat)
y_test=pd.get_dummies(dd_y,columns = list(dd_y.columns)).to_numpy().astype(dtype=float);


# split the dataset
permutation = np.random.permutation(x_train.shape[0]);
x_train=x_train[permutation,:]
y_train=y_train[permutation,:]

# small subset:
subset_size = 2000;
x_train=x_train[:subset_size,:]
y_train=y_train[:subset_size,:]


n_train=x_train.shape[0];

# create tensor variables for data, we do not need gradient w.r.t. to them
t_x_test=torch.tensor(x_test,requires_grad=False,device=device);
t_y_test=torch.tensor(y_test,requires_grad=False,device=device);

#define starting value of weights W for gradient descent
init_std_dev = 0.01;
initialW=init_std_dev*np.random.randn(n_features,n_classes)
# create a PyTorch tensor variable for W and b. 
# we will be optimizing over W, b, finding their best value using gradient descent,
#so we need gradient enabled
W = torch.tensor(initialW,requires_grad=True,device=device);
b = torch.zeros((1,n_classes),requires_grad=True,device=device);
# this optimizer will do gradient descent for us
learning_rate = 0.01;
#optimizer = torch.optim.SGD([W,b],lr=learning_rate)
optimizer = torch.optim.Adam([W,b],lr=learning_rate)
n_epochs = 10000;
batch_size = 256;

for i in range(n_epochs):

    
    permutation = np.random.permutation(x_train.shape[0]);
    x_train=x_train[permutation,:]
    y_train=y_train[permutation,:]

    accuracy = 0.0;

    #looping over batch_size
    for j in range(0,n_train,batch_size):
        t_x_train = torch.tensor(x_train[j:j+batch_size,:],requires_grad=False,device=device);
        t_y_train = torch.tensor(y_train[j:j+batch_size,:],requires_grad=False,device=device);

        # clear previous gradient calculations
        optimizer.zero_grad();
        
        # calculate model predictions
        linear_predictions = torch.matmul(t_x_train,W)+b
        activations =  torch.exp(linear_predictions);
    
        #Passing through softmax
        sum_activations = torch.sum(activations,dim=1,keepdim=True)
        normalized_activations = torch.div(activations, sum_activations);
        cross_entropy_loss = torch.sum(torch.multiply(t_y_train,torch.log(normalized_activations)),dim=1 )
        risk = -1.0 * torch.mean(cross_entropy_loss );

        # calculate gradients
        risk.backward();
        
        # take the gradient step
        optimizer.step();
        

        batch_risk=risk.item();

        true_class = np.argmax(t_y_train.detach().cpu().numpy(),axis=1)
        pred_class = np.argmax(normalized_activations.detach().cpu().numpy(),axis=1)
        accuracy += np.count_nonzero(true_class == pred_class);
        
    # calculate test set risk and accuracy
    #  turn off gradeints 
        
    with (torch.no_grad()):
      linear_predictions = torch.matmul(t_x_test,W)+b
      activations =  torch.exp(linear_predictions);
    
      #Passing through softmax
      sum_activations = torch.sum(activations,dim=1,keepdim=True)
      test_normalized_activations = torch.div(activations, sum_activations);
      cross_entropy_loss = torch.sum(torch.multiply(t_y_test,torch.log(test_normalized_activations)),dim=1 )
    
      test_risk = -1.0 * torch.mean(cross_entropy_loss );
    
      test_true_class = np.argmax(t_y_test.detach().cpu().numpy(),axis=1)
      test_pred_class = np.argmax(test_normalized_activations.detach().cpu().numpy(),axis=1)
      test_accuracy = np.count_nonzero(test_true_class == test_pred_class)/test_pred_class.shape[0];
      test_error = 1.0 - test_accuracy;
        
    accuracy = accuracy / float(x_train.shape[0])
    print(i,batch_risk,test_risk.item(),accuracy,test_accuracy)


0 2.294547046047218 2.425946374079032 0.08 0.1274
1 1.9937837170057202 2.47175948969093 0.32 0.1169
2 1.744222345487081 2.4940571635951363 0.52 0.0981
3 1.5263814303120211 2.5333602170198715 0.67 0.0997
4 1.3447337897424199 2.5957184328551497 0.75 0.0995
5 1.1894377111255638 2.675410158510028 0.78 0.0983
6 1.0538092181254628 2.7683579554790487 0.79 0.1004
7 0.9379040087999055 2.867993558804219 0.81 0.1002
8 0.839227743742547 2.9651365800965124 0.84 0.1014
9 0.7526472388110199 3.0544160713935202 0.87 0.1025
10 0.6750141209510179 3.1358496064183536 0.9 0.1024
11 0.605608944303971 3.212277417363773 0.91 0.1048
12 0.5444264307737047 3.2865385526631306 0.92 0.1069
13 0.49089805055381747 3.3601045409017125 0.93 0.1069
14 0.44379357198901487 3.433074080167486 0.95 0.1072
15 0.4018016208822302 3.5048763625079853 0.95 0.1069
16 0.3640189969685646 3.5748580482412704 0.96 0.1062
17 0.3299926046163585 3.6424804236464117 0.97 0.105
18 0.2995018683757367 3.7073652109166595 0.97 0.1053
19 0.272359607

159 0.010603048968514033 5.453944639937909 1.0 0.1015
160 0.010517268480161504 5.458354011356901 1.0 0.1015
161 0.010432623437262731 5.462744018429985 1.0 0.1015
162 0.010349092856111604 5.467114781737336 1.0 0.1015
163 0.010266656252848736 5.471466422577664 1.0 0.1015
164 0.010185293634807985 5.475799076095091 1.0 0.1015
165 0.010104985475166483 5.48011288199873 1.0 0.1015
166 0.010025712711252941 5.484407993681334 1.0 0.1015
167 0.009947456723582096 5.488684574145402 1.0 0.1016
168 0.009870199326232506 5.492942804059694 1.0 0.1016
169 0.00979392275090769 5.49718286848737 1.0 0.1017
170 0.009718609643023542 5.501404967869073 1.0 0.1017
171 0.009644243034403336 5.505609304135776 1.0 0.1017
172 0.009570806351046934 5.5097960907905374 1.0 0.1017
173 0.009498283384613287 5.513965540662137 1.0 0.1017
174 0.009426658297257818 5.518117864122342 1.0 0.1018
175 0.009355915598894921 5.522253268099786 1.0 0.1018
176 0.009286040151646344 5.526371956182848 1.0 0.1018
177 0.009217017146302247 5.530

315 0.0041798578044866894 5.979595778001825 1.0 0.1022
316 0.004161052445702602 5.982224421310664 1.0 0.1021
317 0.004142383902184746 5.9848463736260875 1.0 0.1021
318 0.004123850788761556 5.987461670849203 1.0 0.1021
319 0.004105451741387054 5.990070346093697 1.0 0.102
320 0.004087185410952956 5.99267243724662 1.0 0.102
321 0.004069050464781515 5.995267977640036 1.0 0.102
322 0.004051045589568868 5.997857002314249 1.0 0.1021
323 0.0040331694866573365 6.000439545079231 1.0 0.1021
324 0.004015420876442677 6.0030156397984085 1.0 0.1022
325 0.003997798493253969 6.005585322156496 1.0 0.1022
326 0.0039803010888207315 6.008148623234847 1.0 0.1022
327 0.003962927428749873 6.010705577032894 1.0 0.1022
328 0.003945676299586454 6.0132562158290686 1.0 0.1022
329 0.003928546497202798 6.015800573228914 1.0 0.1022
330 0.003911536833744984 6.018338680889887 1.0 0.1022
331 0.0038946461398384623 6.020870571913361 1.0 0.1022
332 0.003877873257111316 6.02339627711251 1.0 0.1023
333 0.003861217042394197 6

471 0.0023280741733664257 6.325782765063353 1.0 0.1013
472 0.002320743359158434 6.327673354457548 1.0 0.1013
473 0.00231344940918154 6.329560615730492 1.0 0.1013
474 0.002306192066135575 6.33144455970271 1.0 0.1013
475 0.0022989710743321675 6.3333252040615315 1.0 0.1013
476 0.002291786181552112 6.335202556994747 1.0 0.1013
477 0.0022846371365017864 6.337076632245292 1.0 0.1012
478 0.002277523689530248 6.338947441046353 1.0 0.1012
479 0.0022704455953281182 6.340814995992393 1.0 0.1012
480 0.0022634026100455825 6.342679312514674 1.0 0.1012
481 0.0022563944913358397 6.344540398875016 1.0 0.1012
482 0.0022494209999546644 6.346398268518813 1.0 0.1012
483 0.002242481896569683 6.348252932148407 1.0 0.1013
484 0.0022355769474193305 6.35010440419977 1.0 0.1013
485 0.002228705917975976 6.351952694226855 1.0 0.1013
486 0.002221868577951675 6.35379781366806 1.0 0.1013
487 0.002215064695429166 6.3556397762603805 1.0 0.1013
488 0.0022082940444579603 6.357478590204672 1.0 0.1013
489 0.002201556399581

623 0.0015262293695229344 6.5809382491476685 1.0 0.1003
624 0.0015224808537622392 6.582435569093519 1.0 0.1003
625 0.0015187468507130444 6.583930884994611 1.0 0.1003
626 0.0015150272818585519 6.585424202209353 1.0 0.1003
627 0.0015113220700066299 6.586915527328811 1.0 0.1002
628 0.001507631138079667 6.588404865082752 1.0 0.1002
629 0.0015039544104509903 6.58989222316675 1.0 0.1002
630 0.001500291809898336 6.591377603748918 1.0 0.1002
631 0.0014966432617179045 6.59286101691027 1.0 0.1002
632 0.0014930086910718544 6.594342466421095 1.0 0.1001
633 0.001489388024170084 6.595821959092267 1.0 0.1001
634 0.0014857811863813327 6.597299497818187 1.0 0.1001
635 0.0014821881053953714 6.598775091940666 1.0 0.1001
636 0.0014786087075793863 6.600248744887885 1.0 0.1001
637 0.0014750429208252602 6.601720462803034 1.0 0.1002
638 0.0014714906733919563 6.603190251666383 1.0 0.1002
639 0.0014679518944578096 6.6046581166169736 1.0 0.1002
640 0.0014644265120833271 6.60612406370852 1.0 0.1002
641 0.00146091

...

9377 2.7672093729390216e-06 10.633243001563175 1.0 0.0963
9378 2.7658085857706665e-06 10.633576446385254 1.0 0.0963
9379 2.7644085180095384e-06 10.633909889444986 1.0 0.0963
9380 2.7630091693258965e-06 10.634243330743562 1.0 0.0963
9381 2.7616105393433683e-06 10.63457677028209 1.0 0.0963
9382 2.760212627680032e-06 10.634910208061639 1.0 0.0963
9383 2.758815433937309e-06 10.635243644083218 1.0 0.0963
9384 2.7574189577621443e-06 10.635577078347769 1.0 0.0963
9385 2.756023198747078e-06 10.63591051085623 1.0 0.0963
9386 2.754628156540165e-06 10.636243941609468 1.0 0.0963
9387 2.7532338307750253e-06 10.63657737060834 1.0 0.0963
9388 2.7518402210375394e-06 10.636910797853666 1.0 0.0963
9389 2.7504473269480034e-06 10.637244223346245 1.0 0.0963
9390 2.7490551481700156e-06 10.637577647086857 1.0 0.0963
9391 2.747663684287235e-06 10.637911069076269 1.0 0.0963
9392 2.7462729349377236e-06 10.638244489315236 1.0 0.0963
9393 2.7448828997817463e-06 10.638577907804484 1.0 0.0963
9394 2.743493578372987

9526 2.566224177060623e-06 10.682906966002937 1.0 0.096
9527 2.5649265206348176e-06 10.683240154798108 1.0 0.096
9528 2.563629529407634e-06 10.683573341990154 1.0 0.096
9529 2.562333202973837e-06 10.683906527580044 1.0 0.096
9530 2.5610375410336596e-06 10.684239711568722 1.0 0.096
9531 2.5597425431752033e-06 10.684572893957133 1.0 0.096
9532 2.558448209086491e-06 10.684906074746202 1.0 0.096
9533 2.557154538443333e-06 10.685239253936858 1.0 0.096
9534 2.555861530844933e-06 10.685572431529998 1.0 0.096
9535 2.5545691860115085e-06 10.685905607526525 1.0 0.096
9536 2.5532775035589185e-06 10.686238781927326 1.0 0.096
9537 2.551986483086367e-06 10.686571954733283 1.0 0.096
9538 2.5506961243162913e-06 10.686905125945268 1.0 0.096
9539 2.549406426898968e-06 10.687238295564148 1.0 0.096
9540 2.548117390459135e-06 10.687571463590793 1.0 0.096
9541 2.5468290146526193e-06 10.687904630026042 1.0 0.096
9542 2.545541299138576e-06 10.688237794817773 1.0 0.096
9543 2.544254243548406e-06 10.68857095801

9674 2.381225386241444e-06 10.732201799759647 1.0 0.0963
9675 2.380022473391085e-06 10.732534758379261 1.0 0.0963
9676 2.378820176019502e-06 10.732867715509084 1.0 0.0963
9677 2.3776184938002847e-06 10.733200671149893 1.0 0.0963
9678 2.3764174264325587e-06 10.733533625302508 1.0 0.0963
9679 2.37521697357548e-06 10.733866577967747 1.0 0.0963
9680 2.3740171349192922e-06 10.734199529146476 1.0 0.0963
9681 2.3728179101364747e-06 10.734532478839544 1.0 0.0963
9682 2.371619298901728e-06 10.734865427047847 1.0 0.0963
9683 2.3704213008753196e-06 10.735198373772281 1.0 0.0963
9684 2.369223915804114e-06 10.73553131901376 1.0 0.0963
9685 2.3680271432973076e-06 10.735864262773207 1.0 0.0963
9686 2.3668309830595767e-06 10.736197205051562 1.0 0.0963
9687 2.3656354347789445e-06 10.736530145849777 1.0 0.0963
9688 2.3644404981101273e-06 10.736863085168793 1.0 0.0963
9689 2.363246172764462e-06 10.737196023009579 1.0 0.0963
9690 2.362052458402216e-06 10.737528959373103 1.0 0.0963
9691 2.3608593547180746e

9821 2.210838167704411e-06 10.781130984250865 1.0 0.0963
9822 2.209722364970628e-06 10.781463730555522 1.0 0.0963
9823 2.2086071322036288e-06 10.78179647552533 1.0 0.0963
9824 2.207492469093655e-06 10.782129219160753 1.0 0.0963
9825 2.2063783753209596e-06 10.782461961462253 1.0 0.0963
9826 2.205264850630187e-06 10.782794702430241 1.0 0.0963
9827 2.2041518947115807e-06 10.7831274420651 1.0 0.0963
9828 2.203039507262047e-06 10.78346018036719 1.0 0.0963
9829 2.201927687969609e-06 10.783792917336857 1.0 0.0963
9830 2.2008164365478246e-06 10.784125652974414 1.0 0.0963
9831 2.1997057527213553e-06 10.784458387152688 1.0 0.0963
9832 2.198595636167122e-06 10.78479111999961 1.0 0.0963
9833 2.197486086593132e-06 10.785123851462886 1.0 0.0963
9834 2.1963771037051726e-06 10.785456581595088 1.0 0.0963
9835 2.1952686872156923e-06 10.785789310396055 1.0 0.0963
9836 2.194160836821596e-06 10.786122037865688 1.0 0.0963
9837 2.193053552216459e-06 10.786454764003905 1.0 0.0963
9838 2.1919468331560274e-06 1

9964 2.0569261896674e-06 10.82870026297021 1.0 0.0963
9965 2.055888950512102e-06 10.829032816919232 1.0 0.0963
9966 2.0548522403891443e-06 10.829365369632306 1.0 0.0963
9967 2.053816059027629e-06 10.829697921110581 1.0 0.0963
9968 2.0527804061111395e-06 10.83003047135511 1.0 0.0963
9969 2.0517452813932025e-06 10.830363020366883 1.0 0.0963
9970 2.050710684585156e-06 10.830695568146801 1.0 0.0963
9971 2.0496766154249853e-06 10.83102811469571 1.0 0.0963
9972 2.0486430736240274e-06 10.831360660014392 1.0 0.0963
9973 2.0476100589036143e-06 10.831693204103567 1.0 0.0963
9974 2.0465775710439187e-06 10.832025747946151 1.0 0.0963
9975 2.0455456098706303e-06 10.832358290555813 1.0 0.0963
9976 2.0445141749318858e-06 10.832690831928891 1.0 0.0963
9977 2.0434832659945363e-06 10.833023372062147 1.0 0.0963
9978 2.042452882807667e-06 10.833355910952735 1.0 0.0963
9979 2.0414230250482004e-06 10.833688448598183 1.0 0.0963
9980 2.0403936924641118e-06 10.834020984996371 1.0 0.0963
9981 2.0393648848011572e

In [19]:
dd_y=pd.DataFrame(data=y_train_cat)
y_train=pd.get_dummies(dd_y,columns = list(dd_y.columns)).to_numpy().astype(dtype=float);

dd_y=pd.DataFrame(data=y_test_cat)
y_test=pd.get_dummies(dd_y,columns = list(dd_y.columns)).to_numpy().astype(dtype=float);


# split the dataset
permutation = np.random.permutation(x_train.shape[0]);
x_train=x_train[permutation,:]
y_train=y_train[permutation,:]

# small subset:
subset_size = 500;
x_train=x_train[:subset_size,:]
y_train=y_train[:subset_size,:]


n_train=x_train.shape[0];

# create tensor variables for data, we do not need gradient w.r.t. to them
t_x_test=torch.tensor(x_test,requires_grad=False,device=device);
t_y_test=torch.tensor(y_test,requires_grad=False,device=device);

#define starting value of weights W for gradient descent
init_std_dev = 0.01;
initialW=init_std_dev*np.random.randn(n_features,n_classes)
# create a PyTorch tensor variable for W and b. 
# we will be optimizing over W, b, finding their best value using gradient descent,
#so we need gradient enabled
W = torch.tensor(initialW,requires_grad=True,device=device);
b = torch.zeros((1,n_classes),requires_grad=True,device=device);
# this optimizer will do gradient descent for us
learning_rate = 0.001;
#optimizer = torch.optim.SGD([W,b],lr=learning_rate)
optimizer = torch.optim.Adam([W,b],lr=learning_rate)
n_epochs = 10000;
batch_size = 256;

for i in range(n_epochs):

    
    permutation = np.random.permutation(x_train.shape[0]);
    x_train=x_train[permutation,:]
    y_train=y_train[permutation,:]

    accuracy = 0.0;

    #looping over batch_size
    for j in range(0,n_train,batch_size):
        t_x_train = torch.tensor(x_train[j:j+batch_size,:],requires_grad=False,device=device);
        t_y_train = torch.tensor(y_train[j:j+batch_size,:],requires_grad=False,device=device);

        # clear previous gradient calculations
        optimizer.zero_grad();
        
        # calculate model predictions
        linear_predictions = torch.matmul(t_x_train,W)+b
        activations =  torch.exp(linear_predictions);
    
        #Passing through softmax
        sum_activations = torch.sum(activations,dim=1,keepdim=True)
        normalized_activations = torch.div(activations, sum_activations);
        cross_entropy_loss = torch.sum(torch.multiply(t_y_train,torch.log(normalized_activations)),dim=1 )
        risk = -1.0 * torch.mean(cross_entropy_loss );

        # calculate gradients
        risk.backward();
        
        # take the gradient step
        optimizer.step();
        

        batch_risk=risk.item();

        true_class = np.argmax(t_y_train.detach().cpu().numpy(),axis=1)
        pred_class = np.argmax(normalized_activations.detach().cpu().numpy(),axis=1)
        accuracy += np.count_nonzero(true_class == pred_class);
        
    # calculate test set risk and accuracy
    #  turn off gradeints 
        
    with (torch.no_grad()):
      linear_predictions = torch.matmul(t_x_test,W)+b
      activations =  torch.exp(linear_predictions);
    
      #Passing through softmax
      sum_activations = torch.sum(activations,dim=1,keepdim=True)
      test_normalized_activations = torch.div(activations, sum_activations);
      cross_entropy_loss = torch.sum(torch.multiply(t_y_test,torch.log(test_normalized_activations)),dim=1 )
    
      test_risk = -1.0 * torch.mean(cross_entropy_loss );
    
      test_true_class = np.argmax(t_y_test.detach().cpu().numpy(),axis=1)
      test_pred_class = np.argmax(test_normalized_activations.detach().cpu().numpy(),axis=1)
      test_accuracy = np.count_nonzero(test_true_class == test_pred_class)/test_pred_class.shape[0];
      test_error = 1.0 - test_accuracy;
        
    accuracy = accuracy / float(x_train.shape[0])
    print(i,batch_risk,test_risk.item(),accuracy,test_accuracy)


0 2.3088670727816463 2.292756720729124 0.08 0.0895
1 2.270366526059105 2.2977610251636698 0.12 0.1116
2 2.235250662585721 2.3050712918151937 0.23 0.13
3 2.2029107946517157 2.313751650894319 0.3 0.1396
4 2.172707345192496 2.3230062516188004 0.31 0.1479
5 2.14406826522098 2.3322231007448506 0.34 0.1573
6 2.11653062446871 2.340985222549 0.36 0.1678
7 2.089749868795238 2.3490432453973256 0.35 0.1712
8 2.0634902975595786 2.356279998757568 0.42 0.1704
9 2.0376061810185644 2.362675747163003 0.44 0.1661
10 2.0120205804021833 2.3682768644342262 0.46 0.1607
11 1.9867052676145038 2.3731759107756702 0.49 0.1532
12 1.961663268971447 2.377496916620013 0.51 0.1492
13 1.9369148128763476 2.381374585005423 0.53 0.1432
14 1.9124863932182063 2.3849409425294392 0.53 0.1401
15 1.8884027728314714 2.3883186658266635 0.53 0.1346
16 1.864682006292275 2.3916168392518165 0.54 0.13
17 1.8413332902934245 2.3949283870388163 0.55 0.1282
18 1.8183571002980035 2.3983293535343617 0.59 0.1251
19 1.7957469123897953 2.4018

159 0.4362404702365527 3.1729842022647534 1.0 0.1119
160 0.43271408729882355 3.17775479036632 1.0 0.1122
161 0.4292270056374419 3.182513518664438 1.0 0.1123
162 0.42577871350309165 3.187260323479024 1.0 0.1124
163 0.4223687062489227 3.191995139017423 1.0 0.1125
164 0.4189964862658885 3.196717899649082 1.0 0.1126
165 0.4156615628251281 3.2014285420152375 1.0 0.1123
166 0.4123634519948925 3.206127006446112 1.0 0.1124
167 0.4091016765076247 3.210813236957505 1.0 0.1126
168 0.40587576594005287 3.2154871844185067 1.0 0.1126
169 0.40268525620467216 3.2201488065057333 1.0 0.1125
170 0.3995296896533171 3.2247980667537544 1.0 0.1124
171 0.3964086150872895 3.229434936067586 1.0 0.1125
172 0.39332158755553115 3.2340593928704675 1.0 0.1125
173 0.39026816813147214 3.2386714214920467 1.0 0.1124
174 0.3872479241377832 3.2432710128962148 1.0 0.1125
175 0.3842604288006295 3.2478581621212643 1.0 0.1124
176 0.38130526125237924 3.2524328681098367 1.0 0.1124
177 0.37838200662963706 3.256995134966374 1.0 0.

317 0.15810496727126122 3.7819731924721958 1.0 0.1124
318 0.15731215259878298 3.785024060325595 1.0 0.1124
319 0.15652545834363452 3.7880668421200125 1.0 0.1124
320 0.15574482260375802 3.7911015738701885 1.0 0.1124
321 0.1549701842191297 3.7941282916638497 1.0 0.1124
322 0.15420148279610596 3.7971470304198003 1.0 0.1123
323 0.1534386586996099 3.8001578275158354 1.0 0.1123
324 0.15268165290876262 3.8031607197932646 1.0 0.1123
325 0.15193040712465825 3.8061557403783866 1.0 0.1124
326 0.1511848638990778 3.8091429262846708 1.0 0.1124
327 0.15044496633813864 3.812122312700878 1.0 0.1124
328 0.1497106582316276 3.815093934374137 1.0 0.1124
329 0.14898188412684327 3.8180578267518563 1.0 0.1124
330 0.1482585891381979 3.821014024706609 1.0 0.1124
331 0.14754071907950778 3.823962563194512 1.0 0.1124
332 0.14682822042216276 3.826903476615354 1.0 0.1124
333 0.14612104025074107 3.8298367992655455 1.0 0.1124
334 0.14541912625225784 3.8327625653886868 1.0 0.1124
335 0.14472242680558528 3.8356808086615

479 0.0807613340403744 4.191871400856727 1.0 0.1128
480 0.08048395796888473 4.193983376604753 1.0 0.1128
481 0.08020808226634102 4.196091302132287 1.0 0.1127
482 0.07993369588120727 4.19819519167274 1.0 0.1127
483 0.07966078790931626 4.200295062369074 1.0 0.1127
484 0.07938934750676768 4.202390928580914 1.0 0.1127
485 0.07911936397343075 4.20448280541086 1.0 0.1127
486 0.07885082669858277 4.206570709825398 1.0 0.1127
487 0.0785837251139961 4.208654655477636 1.0 0.1127
488 0.07831804881452575 4.210734657721509 1.0 0.1128
489 0.07805378742939154 4.2128107311214595 1.0 0.1127
490 0.07779093076805178 4.214882891795293 1.0 0.1128
491 0.07752946863432715 4.216951154414848 1.0 0.1128
492 0.07726939097264657 4.219015531946454 1.0 0.1128
493 0.0770106878580312 4.221076041178397 1.0 0.1127
494 0.07675334936032543 4.223132696178919 1.0 0.1127
495 0.07649736569033441 4.225185511496632 1.0 0.1127
496 0.07624272715115302 4.227234500584395 1.0 0.1128
497 0.075989424177008 4.229279678993748 1.0 0.1128

639 0.05005878892232916 4.486901290635186 1.0 0.1126
640 0.04992829321018073 4.488519449378703 1.0 0.1126
641 0.049798332295982274 4.490135274499607 1.0 0.1126
642 0.04966890315578096 4.491748774329437 1.0 0.1125
643 0.04954000278613146 4.493359955164436 1.0 0.1125
644 0.04941162823409892 4.494968824749986 1.0 0.1125
645 0.04928377654214474 4.496575389271104 1.0 0.1125
646 0.049156444798476605 4.498179656272455 1.0 0.1125
647 0.049029630084199353 4.499781633007041 1.0 0.1125
648 0.04890332952308334 4.501381326194025 1.0 0.1126
649 0.048777540250054784 4.502978742379258 1.0 0.1126
650 0.04865225941861004 4.504573888943606 1.0 0.1126
651 0.04852748421359184 4.506166772772408 1.0 0.1126
652 0.04840321181309219 4.507757400442724 1.0 0.1126
653 0.04827943945410739 4.509345779373554 1.0 0.1125
654 0.04815616435071776 4.510931915385928 1.0 0.1125
655 0.048033383778230514 4.512515816909774 1.0 0.1125
656 0.04791109496805297 4.514097489403244 1.0 0.1125
657 0.04778929525902921 4.515676939203865

...

9291 8.87971626566987e-05 8.620093297062747 1.0 0.1153
9292 8.875222415476543e-05 8.620434502817417 1.0 0.1153
9293 8.870730873399055e-05 8.62077570716861 1.0 0.1153
9294 8.866241638548044e-05 8.621116910049066 1.0 0.1153
9295 8.861754709377296e-05 8.621458111571886 1.0 0.1153
9296 8.8572700846623e-05 8.621799311629697 1.0 0.1153
9297 8.852787763188668e-05 8.622140510224686 1.0 0.1153
9298 8.848307743743278e-05 8.62248170735863 1.0 0.1153
9299 8.843830025110905e-05 8.622822903032935 1.0 0.1153
9300 8.839354606075653e-05 8.623164097308534 1.0 0.1153
9301 8.834881485418296e-05 8.623505290126152 1.0 0.1153
9302 8.830410661929938e-05 8.623846481486131 1.0 0.1153
9303 8.825942134397461e-05 8.624187671388572 1.0 0.1153
9304 8.82147590160808e-05 8.624528859833386 1.0 0.1153
9305 8.817011962350905e-05 8.624870046820298 1.0 0.1153
9306 8.81255031541293e-05 8.62521123234888 1.0 0.1153
9307 8.808090959582592e-05 8.62555241641859 1.0 0.1153
9308 8.803633893654663e-05 8.625893599028768 1.0 0.1153
9

9445 8.214144348451932e-05 8.672621882155823 1.0 0.1154
9446 8.209992004079296e-05 8.67296287015121 1.0 0.1154
9447 8.205841787784385e-05 8.673303856796307 1.0 0.1154
9448 8.201693698447426e-05 8.67364484215075 1.0 0.1154
9449 8.197547734946742e-05 8.673985826154443 1.0 0.1154
9450 8.193403896165221e-05 8.674326808807313 1.0 0.1154
9451 8.18926218098641e-05 8.674667790109435 1.0 0.1154
9452 8.185122588296411e-05 8.675008770061027 1.0 0.1154
9453 8.180985116976336e-05 8.67534974866244 1.0 0.1154
9454 8.176849765909067e-05 8.675690725914151 1.0 0.1154
9455 8.172716533982819e-05 8.676031701816749 1.0 0.1154
9456 8.168585420079808e-05 8.67637267549821 1.0 0.1154
9457 8.164456424016465e-05 8.676713647840048 1.0 0.1154
9458 8.160329543750792e-05 8.677054618850306 1.0 0.1154
9459 8.156204778167562e-05 8.677395588536315 1.0 0.1154
9460 8.152082126156436e-05 8.677736556904717 1.0 0.1154
9461 8.14796158660818e-05 8.67807752402138 1.0 0.1154
9462 8.143843158404577e-05 8.678418489831676 1.0 0.1154

9595 7.614469290520577e-05 8.723755739875042 1.0 0.1153
9596 7.610623983027651e-05 8.724096539387896 1.0 0.1153
9597 7.60678064240441e-05 8.724437337711668 1.0 0.1153
9598 7.602939267622838e-05 8.724778134846959 1.0 0.1153
9599 7.599099857653037e-05 8.725118930794391 1.0 0.1153
9600 7.595262411464555e-05 8.72545972561446 1.0 0.1153
9601 7.591426928024824e-05 8.725800519247816 1.0 0.1153
9602 7.58759340630395e-05 8.726141311695004 1.0 0.1153
9603 7.583761845283911e-05 8.726482102956608 1.0 0.1153
9604 7.579932243932147e-05 8.726822893033235 1.0 0.1153
9605 7.576104601218982e-05 8.727163682035576 1.0 0.1153
9606 7.572278916119359e-05 8.727504469854269 1.0 0.1153
9607 7.568455187605755e-05 8.727845256490028 1.0 0.1153
9608 7.564633414657052e-05 8.728186041943582 1.0 0.1153
9609 7.560813596252231e-05 8.72852682621569 1.0 0.1153
9610 7.556995731360847e-05 8.728867609307121 1.0 0.1153
9611 7.553179818960659e-05 8.72920839121867 1.0 0.1153
9612 7.549365858034436e-05 8.729549171951144 1.0 0.11

9746 7.055534607123529e-05 8.775203673207404 1.0 0.1156
9747 7.051974936667614e-05 8.775544305628696 1.0 0.1156
9748 7.048417083658182e-05 8.775884936991629 1.0 0.1156
9749 7.04486104714821e-05 8.77622556729714 1.0 0.1156
9750 7.041306826187351e-05 8.776566196546236 1.0 0.1156
9751 7.037754419831804e-05 8.77690682474 1.0 0.1156
9752 7.034203827127216e-05 8.777247451879573 1.0 0.1156
9753 7.030655047132902e-05 8.77758807796615 1.0 0.1156
9754 7.027108078902397e-05 8.777928703060828 1.0 0.1156
9755 7.023562921479911e-05 8.778269327104887 1.0 0.1156
9756 7.020019573929414e-05 8.778609950099511 1.0 0.1156
9757 7.016478035303336e-05 8.778950571276955 1.0 0.1156
9758 7.012938310230714e-05 8.779291191475396 1.0 0.1156
9759 7.009400392445272e-05 8.779631810628189 1.0 0.1156
9760 7.005864280746418e-05 8.779972428738057 1.0 0.1156
9761 7.002329974195793e-05 8.780313045807608 1.0 0.1156
9762 6.998797471843278e-05 8.780653661839334 1.0 0.1156
9763 6.995266772752842e-05 8.780994276835626 1.0 0.1156

9902 6.521623555690456e-05 8.828330148934242 1.0 0.1156
9903 6.518336260578779e-05 8.828670629391006 1.0 0.1156
9904 6.515050640913924e-05 8.829011108953145 1.0 0.1156
9905 6.511766695815096e-05 8.829351587622012 1.0 0.1156
9906 6.508484424415922e-05 8.829692065398783 1.0 0.1156
9907 6.505203825844926e-05 8.830032542344302 1.0 0.1156
9908 6.5019248992303e-05 8.830373018399435 1.0 0.1156
9909 6.498647643700013e-05 8.83071349356475 1.0 0.1156
9910 6.495372058389141e-05 8.831053967840717 1.0 0.1156
9911 6.492098142426321e-05 8.831394441227708 1.0 0.1156
9912 6.488825894938969e-05 8.831734913726002 1.0 0.1156
9913 6.485555315070264e-05 8.83207538533581 1.0 0.1156
9914 6.48228640194263e-05 8.832415856057276 1.0 0.1156
9915 6.479019154693583e-05 8.832756325890493 1.0 0.1157
9916 6.47575357245243e-05 8.833096794835512 1.0 0.1157
9917 6.472489654357579e-05 8.833437262892346 1.0 0.1157
9918 6.469227399538112e-05 8.833777730171064 1.0 0.1157
9919 6.465966807127631e-05 8.834118196561567 1.0 0.115